# 1. Regression Methods

## 1.1 Processing Stock Price Data in Python

### 1.1.1 Time-series Plot

Let's start with a basic sanity check by visualising the types of the dataset.

In [1]:
%%javascript
MathJax.Hub.Config({
    TeX: { equationNumbers: { autoNumber: "AMS" } }
});

<IPython.core.display.Javascript object>

In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import math
import warnings
from IPython.display import set_matplotlib_formats

%matplotlib inline
set_matplotlib_formats('pdf')
warnings.filterwarnings('ignore')

data = pd.read_csv("data/q1/priceData.csv")
print(data.dtypes)
data.isnull().sum()

date          object
SPX Index    float64
dtype: object


date           0
SPX Index    655
dtype: int64

We see that there are actually 655 null values present in the `SPX Index` column, where we expect a `float64`. Additionally, the `Date` column is not required, so let's get rid of it. The data is not perfectly sequential, so we'll get rid of the entries with `dropna()`.

In [3]:
px = data.drop(['date'], axis=1)
px = px.dropna()
logpx = np.log(px)

figure, axes = plt.subplots(1,2)
figure.suptitle("Price vs Log-price comparison", fontsize=16, fontweight="bold")
figure.set_size_inches(6,3)

px.plot(title="SPX Price", ax=axes[0])
logpx.plot(title="Logarithmic SPX Price", ax=axes[1])
axes[0].grid()
axes[1].grid()

figure.tight_layout()

<Figure size 432x216 with 2 Axes>

We see immediately that there is an upward trend in both graphs, and that applying the natural logarithm suppresses the range of the output, while still preserving order. To draw further observations on the stationarity (or lack thereof) of this time series, let's plot some additional statistics. 

### 1.1.2 Sliding Mean & Variance

A stationary process is a stochastic process whose probability distribution does not change with time. Simply put, this means that measures such as mean and variance should be constant throughout the process. Real data, which we handle throughout this report, is very rarely perfectly in line with this definition, however, and so henceforth we use the term "stationary" loosely to refer to a time-series which has a stable, albeit slightly oscillating mean and tolerable variance.

**(Nothing in the lectures discusses this. What thresholds for mean and variance oscillation do we tolerate before we consider data unsuitable for signal processing? Are there any quantatitive methods to determine confidence in an underlying data set?)

Taking a sliding window of 252 samples, it can be observed that there is an upward trend in the mean with no easily discernable seasonal pattern. Spikes in variance correspond to corrections or market crashes, where large relative daily changes in price are observed. While the standard deviation is relatively stable, oscillating within 0.3, the upward movement in the mean breaks our definition of stationarity, and will require additional mathematical manupulation to remove, which we will explore in upcoming sections.

In [4]:
figure, axes = plt.subplots(nrows=1, ncols=2)
figure.set_size_inches(6,3)
figure.suptitle("SPX 252-day Sliding Statistics", fontsize=16, fontweight="bold")

# Sliding Mean & S.D.
logpx.rolling(252).mean().plot(ax=axes[0], title="Mean")
logpx.rolling(252).std().plot(ax=axes[1], title="Standard Deviation")

axes[0].grid()
axes[1].grid()

figure.tight_layout()

<Figure size 432x216 with 2 Axes>

### 1.1.3 Simple & Log-return Time Series

Comparing the two plots, we see the property of the natural logarithm where $log(1+r) \approx r$ for small approximations around $r = 0$. In fact, the two graphs are almost indistinguishable as daily percentage changes in the S&P500 are usually within this approximation tolerance, except for a few outlying points. 

First-order differencing has successfully de-trended the moving average, and the standard deviation has been reduced by a factor of 10. This time-series is much more stationary as the mean oscillates in very small amplitudes around 0, implying a mean-reverting nature of this time-series. Furthermore, the data in both cases exhibit gaussian properties which further motivate the application of signal processing techniques.

In [5]:
figure.clf()
figure, axes = plt.subplots(nrows=2, ncols=3, constrained_layout=True)
figure.suptitle("Log vs Simple Returns and 252-day Sliding Statistics", fontsize=16, fontweight="bold")
figure.set_size_inches(10,4)

logret = logpx.diff()
simpret = px.pct_change()

for i,daily_returns in enumerate([logret, simpret]):
    name = "Log" if i == 0 else "Simple"
    daily_returns.plot(title="Log-diff Daily Returns", ax=axes[i,0], grid=True)
    daily_returns.rolling(252).mean().plot(title=f"{name} returns: Sliding Mean", ax=axes[i,1], grid=True)
    daily_returns.rolling(252).std().plot(title=f"{name} returns: Sliding S.D.", ax=axes[i,2], grid=True)

figure.tight_layout()

<Figure size 720x288 with 6 Axes>

### 1.1.4 Theoretically justify the suitability of log returns over simple returns for signal processing purposes. Next, perform the “Jarque-Bera” test for Gaussianity on the data, and comment on the results in light of your theoretical answer.

A common assumption in quantitative finance is that prices are log-normally distributed in the short term. Therefore, taking the log of the prices results in normally distributed log-prices.

Signal processing techniques often assume that the samples of the underlying stochastic process is normally distributed, and so we see a good fit when the two contexts are combined.

"Gaussianity", as it is so-called, can be formally tested with the "Jarque-Bera" test which provides a scalar measure of how the skewness and kurtosis of a distribution matches that of a normal distribution, which has skewness $S=0$ and kurtosis $C=3$. 

\begin{equation}
    JB = \frac{n}{6}(S^2 + \frac{(C-3)^2}{4})
\end{equation}

From the definition above, we see that a JB-test value of 0 indicates that the tested data perfectly emulates a normal distribution, and the test value increases as the underlying data deviates further from gaussianity.

In [6]:
from scipy import stats

steps = [i for i in range (21, len(logret.dropna()), 21)]
months = list(map(lambda x: int(x/21),steps))
logdiff_jb_vals = [stats.jarque_bera(logret.dropna()[:step]) for step in steps]
simpret_jb_vals = [stats.jarque_bera(simpret.dropna()[:step]) for step in steps]
logdiff_jbs, logdiff_pvals = map(list, zip(*logdiff_jb_vals))
simpret_jbs, simpret_pvals = map(list, zip(*simpret_jb_vals))

plotted_points = 200
plt.clf()
plt.suptitle("Log vs Simple return JB test values", fontsize="14", fontweight="bold")
plt.ylabel("JB test value")
plt.xlabel("Number of months worth of data")
plt.grid()
plt.plot(months[:plotted_points], logdiff_jbs[:plotted_points], label="Log")
plt.plot(months[:plotted_points], simpret_jbs[:plotted_points], label="Simple")
plt.legend()

results = pd.DataFrame(data={"Months": months, "Log-returns JB": logdiff_jbs, "Log-returns p-value": logdiff_pvals, "Simple returns JB": simpret_jbs, "Simple returns p-values": simpret_pvals})
results = results.set_index("Months")
results.head(10)

Log-returns JB  Log-returns p-value  Simple returns JB  \
Months                                                           
1             1.050136         5.915151e-01           1.043967   
2             0.955807         6.200821e-01           0.914655   
3             1.876383         3.913350e-01           1.810365   
4            12.476409         1.953360e-03          11.268285   
5             8.829944         1.209490e-02           7.989605   
6           192.740162         0.000000e+00         158.937263   
7           147.718908         0.000000e+00         120.286232   
8           148.533099         0.000000e+00         120.821902   
9           111.436987         0.000000e+00          89.782614   
10           67.095226         2.664535e-15          53.405065   

        Simple returns p-values  
Months                           
1                  5.933425e-01  
2                  6.329732e-01  
3                  4.044681e-01  
4                  3.573740e-03  
5                  1.841109e-02  
6                  0.000000e+00  
7                  0.000000e+00  
8                  0.000000e+00  
9                  0.000000e+00  
10                 2.530642e-12

<Figure size 432x288 with 1 Axes>

Jarque-bera test values are computed and plotted for a range of sample data sizes, starting at 21 and increasing by 21 at each step. This approximates an increase of a month's data at each step, since there are approximately 21 trading days in a month. The JB values are consistently trending upward into very large values with the inclusion of more months' data. Simple returns also yield higher JB-test values compared to log-prices, as we would expect. 

We see that even for a single month of data, we approach JB-test values close to or above 1, implying that this "short-term" in which prices may be assumed to be log-normally distributed may be a matter of weeks, and may require data of increased granularity than daily closing prices.

The p-value is the probability of obtaining the observed results given the null hypothesis. Therefore, in this case, our p-values being close to zero for almost every sample size indicates that we have a very strong case against the null hypothesis that these SPX closing prices are normally distributed.

### 1.1.5 You purchase a stock for £1. The next day its value goes up to £2 and the following day back to £1. What are the simple and logarithmic returns over this period and what can you conclude about logarithmic returns on the basis of this example?

We see from the simple script that the price movement that the movement of the log-price matches that of the original price. An increase of $1 (100%) followed by a decrease of the same amount (50%) results in 2 equal and opposite movements of 0.693 in the logarithm. However, the percentage price is different in both cases. Logarithmic returns thus allow us to track and analyse a series of gains and losses in a more symmetric and predictable way than simple returns.

In [7]:
simple_stock_price = pd.DataFrame(data=[1,2,1], columns=["Price"])
simple_stock_price['Simple Return'] = simple_stock_price.pct_change()
simple_stock_price['Log-price Diff'] = np.log(simple_stock_price['Price']).diff()
simple_stock_price.set_index("Price")

Simple Return  Log-price Diff
Price                               
1                NaN             NaN
2                1.0        0.693147
1               -0.5       -0.693147

### 1.1.6 Under what circumstances should you not use log returns over simple returns?

Most models in quantitative finance argue that prices in the short-term are log-normally distributed. Taking log-returns for long-term analysis breaches this assumption and the resulting time series may not be ideal. 

Let us consider the problem of portfolio optimisation using the Markowitz model. We aim to find an optimal weighting vector $w$ across assets to maximise returns while minimising risk (variance). 

Using simple returns, we can easily determine the simple return in our portfolio over time given by the vectorial equation $r_p = w^Tr$. Because of this, we say that simple returns are additive across assets, as we can take the simple returns across all our assets (the vector $r$), scale them by our allocation weights $w$ and determine a simple return for our whole portfolio.

Log-returns cannot be used for this purpose since the weighted average of the log returns across assets does not equal the return of the portfolio.

## 1.2 ARMA vs. ARIMA Models for Financial Applications

### 1.2.1 Plot the S&P500 time-series. Following the process in Question 1.1.1, comment on whether an ARMA or ARIMA model would be more appropriate.

Let's do our usual sanity check of visualising the data and checking for nulls.


In [8]:
import pandas as pd
import matplotlib . pyplot as plt
import numpy as np
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.tsa.ar_model import AR 
import copy
import warnings
warnings.filterwarnings('ignore')

snp = pd.read_csv("data/q1/snp_500_2015_2019.csv", index_col=0)
snp.index = pd.to_datetime(snp.index)

print(snp.isna().sum())
snp.head(5)


High         0
Low          0
Open         0
Close        0
Volume       0
Adj Close    0
dtype: int64


High          Low         Open        Close      Volume  \
Date                                                                         
2015-01-02  2072.360107  2046.040039  2058.899902  2058.199951  2708700000   
2015-01-05  2054.439941  2017.339966  2054.439941  2020.579956  3799120000   
2015-01-06  2030.250000  1992.439941  2022.150024  2002.609985  4460110000   
2015-01-07  2029.609985  2005.550049  2005.550049  2025.900024  3805480000   
2015-01-08  2064.080078  2030.609985  2030.609985  2062.139893  3934010000   

              Adj Close  
Date                     
2015-01-02  2058.199951  
2015-01-05  2020.579956  
2015-01-06  2002.609985  
2015-01-07  2025.900024  
2015-01-08  2062.139893

In [9]:
snp_close = snp["Close"].to_frame().apply(np.log)

figure, axes = plt.subplots(nrows=3, ncols=1)
figure.suptitle("SPX Closing Price & 252-day Sliding Statistics", fontsize=14, fontweight="bold")
figure.set_size_inches(6,6)

axes[0].set_title("SPX closing price")
snp_close.plot(ax=axes[0], grid=True)
axes[1].set_title("Rolling mean")
snp_close.rolling(252).mean().plot(ax=axes[1], grid=True)
axes[2].set_title("Rolling S.D.")
snp_close.rolling(252).std().plot(ax=axes[2], grid=True)

figure.tight_layout()

<Figure size 432x432 with 3 Axes>

We see from the data that this time series is clearly not stationary due to the upward trend that we observed in the previous section, and so an ARIMA method would be more appropriate so that we may skip the hassle of finding an appropriate de-trending solution. We will see that an ARMA model will not be ideal since we are applying it to non-stationary data, which is otherwise a requirement of ARMA models.

### 1.2.2 Fit an ARMA(1, 0) model using the commands below. Plot, in the same figure, both the prediction and the true signal. Inspect the model parameters (model.params). Comment on the results. Are these findings useful in practice?

The model initially looks to be fitting the data very well, but closer inspection shows that the predicted version lags the true signal. We have fit an AR(1) model, whose moving-average component is simple white noise. Therefore, we observe that when large changes occur in the data, a corresponding spike is observed in the residual. 

Interestingly, the residual itself looks like stationary white noise. However, we know as fact that "shocks" occur in the market due to the random availability of new information to investors, and clearly is not correctly modelled by white noise in this case. The JB-test value on the residual clearly reflects this.

In [10]:
snp_arma = copy.deepcopy(snp_close)
snp_arma.columns = ["True"]
model = ARIMA(snp_arma, order=(1,0,0)).fit()
snp_arma["Res"] = model.resid
snp_arma["Prediction"] = snp_arma["True"] - snp_arma["Res"]

figure, axes = plt.subplots(nrows=3, ncols=1)
figure.suptitle("Fitting an ARMA(1) Model to SPX Closing Prices", fontsize=16, fontweight="bold")
figure.set_size_inches(6,6)

axes[0].set_title("ARMA(1,0) model on SPX closing prices")
snp_arma.drop(["Res"], axis=1).plot(ax=axes[0])
axes[1].set_title("Last 50 Samples")
snp_arma.drop(["Res"], axis=1).iloc[-50:].plot(ax=axes[1])
axes[2].set_title("Residual Signal")
snp_arma["Res"].plot(ax=axes[2])
for ax in axes:
    ax.grid()

figure.tight_layout()

residual_jb_vals = stats.jarque_bera(snp_arma["Res"])
results = model.params.to_frame().transpose()
results["JB"] = residual_jb_vals[0]
results

const     ar.L1    sigma2            JB
0  7.748867  0.997354  0.000074  33142.752272

<Figure size 432x432 with 3 Axes>

### 1.2.3 Repeat Question 1.2.2, this time by fitting an ARIMA(1, 1, 0) model. Comment on the results. Compare your results with those in Question 1.2.2. Which analysis is more physically meaningful?

The differencing step by this model removes non-stationary components in the mean of the time-series, as we saw in previous sections. This has removed the initial spike in the residual that we saw previously. We therefore expect the AR model fitted afterwards to perform better than the one in question 1.2.2. 

However, we still observe the same issue as in the last model, where price "shocks" are not modelled by a moving-average component.

In [11]:
snp_arima = copy.deepcopy(snp_close)
snp_arima.columns = ["True"]
model = ARIMA(snp_arima, order=(1,1,0)).fit()
snp_arima["Res"] = model.resid
snp_arima["Prediction"] = snp_arima["True"] - snp_arima["Res"]

figure, axes = plt.subplots(nrows=3, ncols=1)
figure.suptitle("Fitting an ARIMA(1,1,0) Model to SPX Closing Prices", fontsize=16, fontweight="bold")
figure.set_size_inches(6,6)

axes[0].set_title("ARIMA(1,1,0) model on SPX closing prices")
snp_arima.drop(["Res"], axis=1)[1:].plot(ax=axes[0])
axes[1].set_title("Last 50 Samples")
snp_arima.drop(["Res"], axis=1).iloc[-50:].plot(ax=axes[1])
axes[2].set_title("Residual Signal")
snp_arima["Res"][1:].plot(ax=axes[2])
for ax in axes: 
    ax.grid()

figure.tight_layout()

results = model.params.to_frame().transpose()
results["JB"] = stats.jarque_bera(snp_arima["Res"][1:])[0]
results

ar.L1    sigma2          JB
0 -0.00817  0.000074  684.989129

<Figure size 432x432 with 3 Axes>

### 1.2.4 Comment on the necessity of taking the log of the prices for the ARIMA analysis.

As we explored in previous sections, taking the log-difference of two prices is approximate to obtaining the return for a small enough change. Therefore, taking the logarithm of the daily prices before applying an ARIMA model means we are fitting an AR model on the intra-day log-returns of the prices. Physically, this makes more sense as prices are less likely to be historically based, whereas returns might be.

Taking logarithms also increases stationarity by reducing the range of the variance, which we showed in previous sections.

In [12]:
snp_close_log = snp["Close"].to_frame().apply(np.log)
snp_arima_log = copy.deepcopy(snp_close_log)
snp_arima_log.columns = ["True"]
model = ARIMA(snp_arima_log, order=(1,1,0)).fit()
snp_arima_log["Res"] = model.resid
snp_arima_log["Prediction"] = snp_arima_log["True"] - snp_arima_log["Res"]

figure, axes = plt.subplots(nrows=1, ncols=2)
figure.suptitle("Fitting an ARIMA(1,1,0) Model On Closing Log Prices", fontsize=16, fontweight="bold")
figure.set_size_inches(7,3)

snp_arima_log.drop(["Res"], axis=1)[1:].plot(ax=axes[0], grid=True)
snp_arima_log["Res"][1:].plot(ax=axes[1], grid=True)
axes[0].set_title("Prediction")
axes[1].set_title("Residual")

figure.tight_layout()

<Figure size 504x216 with 2 Axes>

## 1.3 Vector Autoregressive (VAR) Models

### 1.3.1 Show that a VAR model can be represented in a concise matrix form $Y = BZ + U$

An autoregressive (AR) process models future values based on the linear combination of past values in a single stochastic process. A vector autoregressive model, by extension, extends this notion by forecasting a future value based on past combinations of multiple processes. It can therefore be expressed in the general form

\begin{equation}
    \textbf{y}_t = \textbf{c} + \textbf{A}_1\textbf{y}_{t−1} + \textbf{A}_2\textbf{y}_{t−2} +···+ \textbf{A}_p\textbf{y}_{t−p} + \textbf{e}_t
\end{equation}

To obtain a more concise form, we can collect the coefficients and process terms into separate matrices like so:

\begin{equation}
    \textbf{B} = 
        \begin{vmatrix}
            \textbf{c} & \textbf{A}_1 & \textbf{A}_2 & ... & \textbf{A}_p 
        \end{vmatrix}
\end{equation}

\begin{equation}
    \textbf{Z} = 
        \begin{vmatrix}
            \textbf{1} & \textbf{y}^T_{t-1} & \textbf{y}^T_{t-2} & ... & \textbf{y}^T_{t-p} 
        \end{vmatrix}
\end{equation}

Now, let $\textbf{Y} = \textbf{y}_t$ and $ \textbf{U} = \textbf{e}_t$, we obtain the equivalent matrix form 

\begin{equation}
    \textbf{Y = BZ + U}
\end{equation}


### 1.3.2 Hence, show that the optimal set of coefficients $B$, denoted by $B_{opt}$, is obtained via $B_{opt} = YZ^T(ZZ^T)^{-1} $

As in the autoregressive model, the matrix $\textbf{U}$ represents the errors (residual) in the model. Treating this as an optimisation problem, we want to find the solution for the equation $\textbf{Y = BZ + U}$ that minimises $\textbf{U}$. 

We solve this minimisation by finding a least-squares estimation for $\textbf{B}$ and minimising the objective.
\begin{equation}
    \textbf{U}^2 = \textbf{(BZ - Y)}^2          \\
    \textbf{U}^2 = \textbf{(BZ - Y)(BZ-Y)}^T    \\
\end{equation}

Since the objective is quadratic and positive, we have a single global minimum and can solve it with a simple first derivative test.

\begin{equation}
    \frac{\delta \textbf{U}^2}{\delta \textbf{B}} = 2\textbf{B}\textbf{Z}\textbf{Z}^T-2\textbf{Y}\textbf{Z}^T = 0 \\
    \textbf{B}\textbf{Z}\textbf{Z}^T=\textbf{Y}\textbf{Z}^T \\
    \textbf{B}_{opt}=\textbf{Y}\textbf{Z}^T (\textbf{Z}\textbf{Z}^T)^{-1} \\
\end{equation}

### 1.3.3 Elaborate on how, for stability, all the eigenvalues of the matrix A must be less
than 1 in absolute value.

A VAR(1) process can be written out further using its recursive definition:

\begin{equation}
    \textbf{y}_t = \textbf{A}\textbf{y}_{t-1} + \textbf{e}_t \\
    \textbf{y}_t = \textbf{A}(\textbf{A}\textbf{y}_{t-2}+\textbf{e}_{t-1}) + \textbf{e}_t \\
    \textbf{y}_t = \textbf{A}^2\textbf{y}_{t-2}+\textbf{A}\textbf{e}_{t-1} + \textbf{e}_t \\
    ... \\
    \textbf{y}_t = \textbf{A}^p \textbf{y}_{t-p} + \sum_{i=0}^{p-1} \textbf{A}^i \textbf{e}_{t-i} \\
\end{equation}

Therefore, if the eigenvalues of the matrix \textbf{A} are larger than 1, that means that terms will grow exponentially as the matrix gets successively applied at each time step. For numerical stability and convergence, we thus require the eigenvalues of \textbf{A} to be below 1.

### 1.3.4 Consider the time-series of the stocks with tickers CAG, MAR, LIN, HCP, MAT, and detrend them using an MA(66) model (66 corresponds to 3 × 22, i.e. one quarter). Elaborate on whether it would make sense to construct a portfolio using these stocks? Why? Comment on your results.

In [13]:
import pandas as pd
import matplotlib.pyplot as plt 
import numpy as np
from statsmodels.tsa.api import VAR
import warnings
warnings.filterwarnings('ignore')

df = pd.read_csv('data/q1/snp_allstocks_2015_2019.csv')
df = df.set_index('Date')
df.index = pd.to_datetime(df.index)

info = pd.read_csv('data/q1/snp_info.csv')
info.drop(columns=info.columns[0], inplace=True)

# Consider the time-series of the stocks with tickers CAG, MAR, LIN, HCP, MAT, and detrend them using an MA(66) model (66 corresponds to 3 × 22, i.e. one quarter), that is, run
tickers = ['CAG' , 'MAR' , 'LIN' , 'HCP' , 'MAT']
stocks = df[tickers]
stocks_ma = stocks.rolling(window=66).mean()
stocks_detrended = stocks.sub(stocks_ma).dropna()

figure, axes = plt.subplots(nrows=1, ncols=2)
figure.suptitle("De-trending 5 Select Stocks", fontsize=16, fontweight="bold")
figure.set_size_inches(8,3)
figure.tight_layout()
stocks.plot(grid=True, title='Stock Prices', ax=axes[0])
stocks_detrended.plot(grid=True, title='De-trended Stocks Prices', ax=axes[1])

figure.tight_layout()

<Figure size 576x216 with 2 Axes>

In [14]:
# Now, fit a VAR(1) model to these time-series and compute the eigenvalues of the regression matrix A, by:
model = VAR(stocks_detrended)
results = model.fit(1)
results.params[1:].transpose()

L1.CAG    L1.MAR    L1.LIN    L1.HCP    L1.MAT
CAG  0.872786 -0.063745  0.000134 -0.084776  0.643072
MAR  0.113179  0.895820 -0.111678 -0.083831  0.094931
LIN -0.281265 -0.184820  0.704023 -0.401417  2.033036
HCP  0.011912 -0.005004  0.004982  0.931708 -0.012884
MAT  0.058776  0.022917 -0.025557 -0.046406  0.802974

Fitting the VAR(1) model and inspecting the model parameters tells an interesting story: The forecasted value of a given stock is mostly comprised of its previous value, with small inputs from other stocks. Intuitively, this tells us that the stocks are largely uncorrelated, with the exception of LIN and MAT, which could be due to LIN having very little data available compared to the other stocks. 

The parameters are physically quite related to covariances, since each coefficient represents "how much" of the lagged variable contributed to the present value. We also observe empirically that the diagonals contain the largest values, which we expect in a "covariance" matrix. 

In [15]:
A = results.params[1:].values
eigA, _ = np.linalg.eig(A)
print("Eigenvalues:", eigA)
print("Average: ", np.mean(eigA))
print("Max: ", np.max(eigA))
print("Min: ", np.min(eigA))

Eigenvalues: [0.71449288+0.12927613j 0.71449288-0.12927613j 1.00635964+0.j
 0.86051894+0.j         0.91144512+0.j        ]
Average:  (0.8414618919995345+0j)
Max:  (1.00635964046102+0j)
Min:  (0.7144928806785384-0.12927612512613001j)


Performing eigenvector analysis on this "matrix" yields an interesting result: The largest eigenvalue is 1.006, which means the largest possible "variance" one can incur from a portfolio constructed from these stocks is 1.006 and the average eigenvalue is 0.841. The "covariance" matrix shows us that the stocks are largely uncorrelated, and so constructing a portfolio from these may be a sensible choice. However, these dimensionless values do not have much meaning on their own, so in the next section we will explore the same analyses across industry sectors.

### 1.3.5 With the aid of snp_info.csv, repeat Question 1.3.4 but this time by selecting the tickers according to their sector

In [16]:
import warnings
warnings.filterwarnings('ignore')

mean_eigens = []
max_eigens = []
num_stonks = []

for sector in info['GICS Sector'].unique():
    tickers = info.loc[info['GICS Sector']==sector]['Symbol'].tolist()
    stocks = df[tickers]
    stocks_ma = stocks.rolling(window=66).mean()
    stocks_detrended = stocks.sub(stocks_ma).dropna()

    model = VAR(stocks_detrended)
    results = model.fit(1)
    results.params[1:].transpose()
    A = results.params[1:].values
    eigA, _ = np.linalg.eig(A)
    
    mean_eigens += [eigA.mean()]
    max_eigens += [eigA.max()]
    num_stonks += [len(tickers)]

results = pd.DataFrame(info['GICS Sector'].unique(), columns=["Sector"])
results['Max Eigenval'] = max_eigens
results['Mean Eigenval'] = mean_eigens
results['# of Stocks'] = num_stonks
results

Sector        Max Eigenval       Mean Eigenval  \
0              Industrials  0.991568+0.017404j  0.750818-0.000000j   
1              Health Care  0.993598+0.033204j  0.441843+0.000000j   
2   Information Technology  0.992075+0.036269j  0.803445+0.000000j   
3   Communication Services  0.982234+0.007508j  0.925770+0.000000j   
4   Consumer Discretionary  0.989860+0.039565j  0.804006-0.000000j   
5                Utilities  0.983506+0.064941j  0.463644+0.000000j   
6               Financials  1.003000+0.051864j  0.418911+0.000000j   
7                Materials  0.990101+0.057061j  0.481792-0.000000j   
8              Real Estate  0.982744+0.009006j  0.918568-0.000000j   
9         Consumer Staples  0.991324+0.019122j  0.849384+0.000000j   
10                  Energy  0.985577+0.000000j  0.929837+0.000000j   

    # of Stocks  
0            69  
1            62  
2            68  
3            26  
4            65  
5            27  
6            68  
7            26  
8            31  
9            33  
10           30

We now automate the eigenvalue analysis across the sectors. We started with a hypothesis that investing across a single sector should be worse than our original porfolio in the previous section, since stocks in the same sector should have a higher correlation. We see however that this is untrue, as the maximum eigenvalues are all lower than that of the previous stock spread. 

This could be due to a number of factors, as the S&P 500 contains many large-cap companies in each sector, each of which may have disjoint business concerns within the sector which may reduce correlation between company stock performance. Additionally, the number of stocks in each sector is much larger than the previous selection of only 5 stocks. The mean eigenvalue differs greatly across sectors. For example, healthcare and utilities have he lowest mean eigenvalues at 0.442 and 0.464 respectively compared to a traditionally "risky" sector such as real estate at 0.919. 

Investing in one of these sectors thus might be less risky in the mean-variance portfolio optimisation sense than the 5-stock portfolio mentioned previously.

# 2. Bond Pricing

## 2.1 Examples of Bond Pricing

### 2.1.1 An investor receives USD 1,100 in one year in return for an investment of USD 1,000 now. Calculate the percentage return per annum with: a) Annual compounding, b) Semiannual compounding, c) Monthly compounding, d) Continuous compounding

The effective interest rate is defined as the real return of any interest-paying investment when the effects of compounding over time are taken into account, and is given by 

\begin{equation}
    1 + r_{eff} = (1 + \frac{r}{n})^n 
\end{equation}


In any case of compounding period, the interest he receives is a total of $100 dollars, and therefore the effective interest rate is fixed at 10%. The annual interest rate offered can therefore be computed in reverse with 

\begin{equation}
    r = n[(1 + r_{eff})^\frac{1}{n} - 1]
\end{equation}

* Under annual compounding, his annual return is simply $10\%$, since there is only 1 compounding period.
* Under semi-annual compounding, the effective rate is $2[(1.1)^\frac{1}{2} - 1] = 9.76\%$
* Under monthly compounding, the effective rate is $12[(1.1)^\frac{1}{12} - 1] = 9.57\%$
* Continuous compounding is where the number of compounding periods $n$ approaches infinity, leaving us with $lim_{m->\infty} (1+\frac{r}{m})^{mt} = e^{rt}$. Under continuous compounding, the effective rate is therefore $ln(1.1) = 9.53\%$

### 2.1.2 What rate of interest with continuous compounding is equivalent to 15% per annum with monthly compounding?

We simply solve for two equal effective rates:
`
\begin{equation}
    (1 + \frac{0.15}{12})^{12} - 1 = e^r\\
    1.1608 = e^r \\
    r = ln (0.2608) = 14.9\%
\end{equation}

### 2.1.3 A deposit account pays 12% per annum with continuous compounding, but interest is actually paid quarterly. How much interest will be paid each quarter on a USD 10,000 deposit?

The payment is simply calculated with continuous compounding as $P = \$X * (e^{0.12 * 0.25} -1)$ where $P$ is the payment received and $X$ is the current balance in the account, including previous payouts.

- Q1: $P_1 = \$10000 * (e^{0.12 * 0.25} -1) = \$304.55$
- Q2: $P_2 = \$(10000 + P_1) * (e^{0.12 * 0.25} -1) = \$313.82$
- Q3: $P_3 = \$(10000 + + P_1 + P_2) * (e^{0.12 * 0.25} -1) = \$323.38$
- Q4: $P_4 = \$(10000 + + P_1 + P_2 + P_3) * (e^{0.12 * 0.25} -1) = \$333.23$

## 2.2 Forward rates

Suppose that the one–year interest rate, $r_1$ is 5%, and the two–year interest rate, $r_2$ is 7%. 
If you invest USD 100 for one year, your investment grows to $100 × 1.05 = USD 105$.
If you invest for two years, it grows to $100×1.07^2 = USD 114.49$. 
The extra return that you earn for that second year is $1.07^2/1.05−1 = 0.090 = 9.0 \%$.

### 2.2.1 Would you be happy to earn that extra 9% for investing for two years rather than one?
By construction, the forward rate implies a no-arbitrage scenario: the rate is calculated based on committing to lend the proceeds of the first year's investment for a year, a year from now. Therefore, there is no difference in profit whether I invest for one year or two. If any strategy resulted in a higher gain, there would exist an arbitrage opportunity in which we could borrow money at the less profitable rate, and lend the proceeds at the advantageous rate which allows us to pay back the borrowed amount and take a profit without having engaged in any risk-taking.

### 2.2.2 Comment on the 5%, 7%, and 9% investment strategies.
No strategy is any more optimal than another at this point, since all rates are based on present interest rates in a no-arbitrage environment. However, the difference between the three choices arises through interest rate fluctuation.

A shorter commitment might therefore be better as the 2-year commitment may be suboptimal if a better opportunity were to arise in the time. Conversely, if interest rates were to fall within the first year, locking in this 2-year commitment may be an ideal decision. This reinforces the previous point: some measure of risk must be taken in order to potentially yield the maximum profit.

### 2.2.3 Comment on the advantages and disadvantages of the forward rate of 9%.
The forward rate is calculated based on the current interest rates and is thus subject to interest rate fluctuation. It still carries the same commitment as the %7\%$ two-year rate, since we would have to commit to investing the returns of a 1-year investment for a year, a year from now to obtain it.

However, it does at least give us an idea of how our borrower perceived interest rate movement. A forward rate of 9\% implies that the 1-year interest rate next year is 9\%, almost double of this year's 5\% interest rate.

### 2.2.4 How much would you need to go from 1y investment to 2y investment and what does it depend upon?
Provided the interest rate does not change, no money is needed to translate between the two investments.

## 2.3 Duration of a Coupon-bearing Bond

### 2.3.1 Calculate the Duration of the 1% 7-year bond in the table.
The terms of the duration have been calculated for us in the last row of the table, and so the answer is attained with a simple summation:

\begin{equation}
    0.0124 + 0.0236 + 0.0337 + 0.0428 + 0.0510 + 0.0583 + 6.5377 = 6.7595 
\end{equation}

### 2.3.2 Calculate the modified duration of the bond.

Since the annual yield to maturity is 5%, under annual compounding, the modified duration is obtained by

\begin{equation}
    D_m = \frac{D}{1 + {0.05}} = \frac{6.7595}{1.05} = 6.438
\end{equation}

It can be shown by differentiating the price of a bond with respect to its yield that the modified duration is actually the negated first derivative of price w.r.t. yield.

### 2.3.3 Explain why duration (or modified duration) are convenient measures to protect the pension plan against unexpected changes in interest rates.

The yield-to-maturity (YTM) of a bond is defined as the annual effective interest rate which, when used to discount from the maturity date of the bond to the present, results in the current price. Bond price and yield are therefore inversely proportional, and the latter determines the price of the bond. YTM is often closely tied to federal interest rates (following a no-arbitrage theory), and interest rate fluctuation can thus result in an unexpected fluctuation in asset value for bond holders.

Therefore, one way to protect a given investment against interest rate changes is a process called immunisation, which matches the price and duration of a constructed portfolio with the price and duration of a given financial commitment. This works on the concept of Taylor Series approximation: we create a portfolio that matches the terms in the expansion of a commitment's price at current interest rates, so that the portfolio approximates and emulates the price movements of the commitment and therefore matches its value at all times.

\begin{equation}
    P(\lambda) = P(\lambda_0) + \frac{dP(\lambda_0)}{d\lambda}(\lambda - \lambda_0) + \frac{1}{2}\frac{d^2P(\lambda_0)}{d\lambda^2}(\lambda - \lambda_0)^2 + ...
\end{equation}

Since we established that the (modified) duration is simply the negated first derivative of the price, matching the present value and duration thus matches up to the first-order term in this approximation. In theory, higher order terms (such as second-order convexity, shown above) can be matched to attain better approximations. In practice, the underlying portfolio needs to be rebalanced every so often to ensure that the portfolio is still matched to the original commitment under refreshed market conditions.


## 2.4 Capital Asset Pricing Model (CAPM) and Arbitrage Pricing Theory (APT)

Here, we will explore the performance of 157 European company stocks from the period 2017-2019. We begin by visualising and cleaning the data first. Since the data is on daily returns, where invalid `NaN` values exist, they will be replaced with a daily return of 0.

In [17]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
%matplotlib inline

df = pd.read_csv(r'data/q2/fsp_case_31_BSD.csv',index_col=0,header=[0,1])
df.index = pd.to_datetime(df.index)
df = df.sort_index()

print("# of NaN values in returns before cleaning: ", df['ret'].transpose().isna().sum().sum())
print("# of NaN values in mcap before cleaning: ", df['mcap'].transpose().isna().sum().sum())

df_filled = df.fillna(0)        # We'll primarily use this
df_dropped = df.dropna(1)       # This will be necessary for APT calculations later

# of NaN values in returns before cleaning:  4220
# of NaN values in mcap before cleaning:  4220


### 2.4.1 Estimate the market returns per day.

For un-weighted market returns, we can simply take the average returns of all companies in the market, giving the market returns. Without considering weighting (i.e. if we were to construct a portfolio of equally allocated investments in all companies), our cumulative return is quite dismally close to 0.

In [18]:
# Estimate the market returns per day: un-weighted average return across all companies
unweighted_returns = df_filled['ret'].mean(1)

fig, (ax1, ax2) = plt.subplots(2,1)
fig.suptitle("Equally-weighted Portfolio Performance", fontsize=16, fontweight="bold")
unweighted_returns.plot(ax=ax1, grid=True)
unweighted_returns.cumsum().plot(ax=ax2, grid=True)

ax1.set_title("Daily Market Returns")
ax2.set_title("Cumulative Daily Market Returns")
fig.set_size_inches(6,4)
fig.tight_layout()

<Figure size 432x288 with 2 Axes>

### 2.4.2 Estimate a rolling (sliding) beta, $\beta_{i,t}$, for every company i, with the rolling window of 22 days. (Hint: Estimate time series of $\beta_{i,t}$ with respect to the market, comment on the volatility of $\beta_{i,t}$)

The beta of a given stock is given by the ratio of a given asset's covariance to the variance of the market, and therefore the formula below.

\begin{equation}
    \beta_i = \frac{cov(a_i, market)}{cov(market, market)} = \frac{\sigma_{iM}}{\sigma^2_M}
\end{equation}

Thus far, we have assumed the "market portfolio" to be an equally-weighted portfolio of all securities in the market. We will continue with this assumption for now, noting that this is not actually the standard definition of the market portfolio (which we will explore in the next section).

Calculating a 22-day (1 trading month) rolling beta requires us to perform the above computation in a rolling window of the 22 previous days. We create a new time-series by appending the daily un-weighted market returns to daily returns of all company stocks, and iterate over it starting at the 22nd entry as follows:

In [19]:
"""
Compute 22-day covariance with Market, then normalise by market variance.
We'll put make this a function of the market returns, so that we can calculate 
it again later using the cap-weighted market returns.
"""
def calc_betas(market_returns, use_filled=True, **kwargs):
    title = kwargs["title"] if "title" in kwargs else ""
    data = df_filled['ret'].copy() if use_filled else df_dropped['ret'].copy()
    data["market"] = market_returns
    data.index = pd.to_datetime(data.index)

    unweighted_betas = pd.DataFrame(columns=data.columns)

    for time in data.index[21:]:
        covariances = data[:time].iloc[-22:].cov()
        unweighted_betas.loc[time] = covariances["market"] / covariances["market"]["market"]

    if title:
        fig = plt.figure()
        fig.suptitle(title, fontsize=16, fontweight="bold")
        spec = gridspec.GridSpec(ncols=3, nrows=1, figure=fig)
        ax1 = fig.add_subplot(spec[0, 0:2])
        ax2 = fig.add_subplot(spec[0, 2])
        fig.set_size_inches(10,4)
        ax1.grid()
        ax2.grid()

        ax1.plot(unweighted_betas)
        ax1.set_ylabel('Beta')
        ax1.set_xlabel('Date')
        ax1.set_title('22-Day Rolling Betas')

        ax2.hist(unweighted_betas.values.reshape(-1), bins=60)
        ax2.set_ylabel('Count')
        ax2.set_xlabel('Beta')
        ax2.set_title('Beta Distribution')

        fig.tight_layout()

        print('mean: ', np.mean(unweighted_betas.values.reshape(-1)))
        print('std: ', np.std(unweighted_betas.values.reshape(-1)))

    return unweighted_betas

# Calculate rolling 22-day betas for each stock using the equally-weighted portfolio as the "market portfolio".
unweighted_betas = calc_betas(unweighted_returns, title="Unweighted Rolling Beta Analysis")

mean:  1.0
std:  0.771809337777677


<Figure size 720x288 with 2 Axes>

Based on this calculation, we observe that the stocks are on average perfectly correlated with the market (which we expect by definition, since the market is comprised of only the full collection of all stocks), and that the average stock is about 77% more volatile than the market. Since null values were replaced with padded zeroes, we notice an uncharacteristic spike in the distribution at 0, since 4220 entries were replaced.

### 2.4.3 Estimate the cap-weighted market return: the capitalisation-weighted daily average return across all companies.

Instead of allocating our portfolio evenly throughout all assets in the market (as in the previous example of un-weighted averages), we now instead allocate an investment in each asset based on how large it is in the market (by capital value). The weighting coefficient $w_i$ is thus created for each asset by taking the company's value as a fraction of the total market value. This is what is known by definition as the market portfolio, and its return is given by the following summation:

\begin{equation}
    r_m = \sum_i \frac{mcap_i}{\sum_i mcap_i}r_i = \sum_i w_ir_i
\end{equation}

The market portfolio is the basis of the one-fund theorem, and by extension, the efficient market hypothesis. The latter states that all assets are fairly priced due to many efficient participants in the market removing any arbitrage opportunities. Therefore, an optimal investment strategy is to simply create a portfolio by a combination of buying and selling the market portfolio and at the risk-free rate.

In [20]:
market_returns = df_filled['ret'].multiply(df_filled['mcap'])       # Daily return per company, element-wise multiplication with market cap
total_market_caps = df_filled['mcap'].sum(axis=1)            # Daily total market values
market_returns = market_returns.sum(axis=1).divide(total_market_caps)  # Sum across companies and divide by total market cap

fig, (ax1, ax2) = plt.subplots(2,1)
fig.suptitle("Market Portfolio Performance", fontsize=16, fontweight="bold")
market_returns.plot(ax=ax1, grid=True)
market_returns.cumsum().plot(ax=ax2, grid=True)
fig.set_size_inches(6,4)
ax1.set_title("Daily Returns")
ax2.set_title("Cumulative Daily Returns")
fig.tight_layout()

<Figure size 432x288 with 2 Axes>

We see immediately that investing in the market portfolio yields better results, giving us a cumulative return of about 10% over 2 years. Intuitively, this could be attributed to the efforts of efficient investors allocating their capital to the best-performing companies, and therefore companies which are more likely to succeed naturally occupy a larger fraction of the market, and thus the market portfolio.

### 2.4.4 Estimate a rolling $\beta_{mi,t}$ like in Part 2 above but with the market return from Part 3. Compare the two betas in Part 2 and Part 4, that is, the equally-weighted $\beta_M$ and the cap–weighted $\beta_M$.

We can now consider the standard definition of the beta of a stock. The formula remains the same, but the variance of the market is now calculated on the market portfolio instead of the equally-allocated portfolio previously. 

In [21]:
betas = calc_betas(market_returns, title="Cap-weighted Beta Analysis")

mean:  0.907195049074898
std:  0.7140074309062413


<Figure size 720x288 with 2 Axes>

We observe that the average beta is no longer 1, but 0.907 which implies that a given company is slightly less volatile than the market portfolio on average. The standard deviation has also decreased from 0.77 to 0.71 once we consider cap-weighted market returns, since the effects of smaller, more volatile companies are reduced by the weighting coefficient.

### 2.4.5 Arbitrage Pricing Theory

Arbitrage Pricing Theory (APT) states that the expected return of a risky asset can be expressed as a linear combination of systematic factors, a constant and a term characterising idiosyncratic behaviour: 

\begin{equation}
    r_j = a_j + b_{j1}F_1 + b_{j2}F_2 + ... +  b_{jn}F_n + \epsilon_j
\end{equation}

In this example, we aim to investigate if a 2-factor model sufficiently describes the prices of companies in this time-series dataset. We begin by assuming that the return of a given asset is tied to two factors: the market return and the asset's size in the market.

In finance, risk is often characterised as qualitatively characterised as systemic (risk that is inherent to the financial system) and idiosyncratic (risk that is unique to the asset). The regressed values $R_m, R_s$ and $a$ in this model are characteristic of returns gained from systematic risk, and the stock's idiosyncratic return is within the error term $\epsilon_i$.

Therefore, a given asset return will be affected by the market return $R_m$ with a sensitivity $b_{m,j}$, while the market capitalisation of the stock will have some factor return $R_s$ with a sensitivity of $b_{s, j}$. Following the intuitions of an efficient, no-arbitrage market, our stocks should reward us with some returns for taking risk over simply lending at the risk free rate, so we can interpret our constant $a_j$ as some abstract representation of the risk-free rate ($r_f$), which is uniform across all securities and we therefore have a single constant $a$. Our specific factor model can therefore be defined as

\begin{equation}
    r_j = a + b_{m,i}R_m + b_{s,i}R_s + \epsilon_j
\end{equation}

Expressed in matrix form for all securities, this becomes 

\begin{equation}
    \textbf{r} = \textbf{A} \textbf{x} + \textbf{e}
\end{equation}

\begin{equation}
    \begin{vmatrix}
        r_1 \\
        r_2 \\
        ... \\
        r_n \\
    \end{vmatrix} =  
    \begin{vmatrix}
        1 & b_{m,1} & b_{s,1}\\
        1 & b_{m,2} & b_{s,2}\\
        ... & ... & ... \\
        1 & b_{m,n} & b_{s,n}\\
    \end{vmatrix}
    \begin{vmatrix}
        a \\
        R_m \\
        R_s \\
    \end{vmatrix} +
    \begin{vmatrix}
        \epsilon_1 \\
        \epsilon_2 \\
        ... \\
        \epsilon_n \\
    \end{vmatrix}     
\end{equation}

To determine the coefficients in $\textbf{A}$, we assume that the sensitivity to market returns for a given stock is its 22-day rolling beta, which we calculated previously. For the sensitivity to size, we use $b_{s,i} = ln(size)$. We can therefore regress values for $a$, $R_m$ and $R_s$ every day using the ordinary least-squares method.

\begin{equation}
    \textbf{x} = (\textbf{A}^T\textbf{A})^{-1}\textbf{A}^T\textbf{r}
\end{equation}

In [22]:
import warnings
warnings.filterwarnings('ignore')

# We have to omit 0 entries here, otherwise applying logs will give -infinity values.
indices = df_dropped.index.intersection(betas.index)

# Re-calculate betas with only these indices
bm = calc_betas(market_returns, use_filled=False).iloc[:, :-1]
bm = bm.loc[indices]

bs = np.log(df_dropped["mcap"].loc[indices])
r = df_dropped["ret"].loc[indices]

Rm = pd.Series(index=r.index)
Rs = pd.Series(index=r.index)
a = pd.Series(index=r.index)
e = pd.DataFrame(index=r.index, columns=r.columns)

for j in r.index:
    r_j = r.loc[j].values.reshape(-1,1)
    bm_j = bm.loc[j].values.reshape(-1,1)
    bs_j = bs.loc[j].values.reshape(-1,1)
    ones = np.ones((r_j.shape))
    A = np.hstack((ones, bm_j, bs_j))

    x = np.linalg.inv(A.T.dot(A)).dot(A.T).dot(r_j)
    
    a[j] = float(x[0])
    Rm[j] = float(x[1])
    Rs[j] = float(x[2])
    e.loc[j] = (r_j-A.dot(x)).reshape(1,-1)

#### 2.4.5.b Comment on the magnitude and variance of $r_f$, $R_m$, and $R_s$.

From earlier calculations, we know that the market portfolio gained a cumulative return of about 10% in this time. Despite this, none of the regressed variables are significantly positive, and are largely zero-mean variables with large variances. None of these variables therefore are effectively capturing the upward trend of the market. To confirm this result, we check the idiosyncratic return in the next section.

In [23]:
fig, (ax1, ax2, ax3) = plt.subplots(3,1)
fig.suptitle("2-Factor Pricing Model Parameters", fontsize=16, fontweight="bold")
Rm.plot(legend=False, ax=ax1, title='Market Returns', grid=True)
Rs.plot(legend=False, ax=ax2, title='Size Returns', grid=True)
a.plot(legend=False, ax=ax3, title='Alpha', grid=True)

fig.set_size_inches(6,5)
fig.tight_layout()

ParamsStats = pd.DataFrame(index=['Rm','Rs','a'], columns=['Mean', 'S.D.', '|S.D. / Mean|'])
ParamsStats.loc['Rm'] =[Rm.mean(), Rm.std(), abs(Rm.std()/Rm.mean())]
ParamsStats.loc['Rs'] =[Rs.mean(), Rs.std(), abs(Rs.std()/Rs.mean())]
ParamsStats.loc['a'] =[a.mean(), a.std(), abs(a.std()/a.mean())]

ParamsStats

Mean      S.D. |S.D. / Mean|
Rm -0.000288  0.007871      27.28415
Rs  0.000193  0.001733      8.962991
a  -0.004234  0.041209      9.731747

<Figure size 432x360 with 3 Axes>

#### 2.4.5.c Find the correlation through time for every company, that is, $ <\epsilon_i,r_i >$, where $\epsilon_i$ is called the specific return.

Recall that the specific return $\epsilon_i$ is the return that is characteristic of the individual stock and not explained by the factor model. Therefore, if the 2-factor model adequately explains the returns of assets over time, we expect $\epsilon$ to be, on average, quite small in magnitude and zero-mean.

However, comparing returns and specific returns in a scatter plot and histogram reveals that $\epsilon$ is very highly correlated to the returns, and the scatter pattern follows the line through the origin quite closely. The average correlation is 0.81 with only a 10.3% normalised deviation. The two-factor model is thus inadequate to model the returns over time of our assets.

In [24]:
from scipy.stats import pearsonr
corrs = pd.Series(index=e.columns)

fig, (ax1, ax2) = plt.subplots(1,2)
fig.suptitle("Relationship Between Specific and Normal Returns", fontsize=16, fontweight="bold")
fig.set_size_inches(7,3)

for company in e.columns:
    ax1.plot(e[company], r[company], '*')
    # TODO: What's the difference between this and np.correlate?
    corrs[company] = pearsonr(e[company], r[company])[0]

ax1.plot(e.values.reshape(-1),e.values.reshape(-1), color='black')
ax1.grid()

ax1.set_title('Scatter Plot')
ax1.set_xlabel('Specific Returns')
ax1.set_ylabel('Returns')

corrs.hist(bins=20, ax=ax2)
ax2.set_title('Correlation Histogram')
ax2.set_xlabel('Correlation')
ax2.set_ylabel('Count')
pd.Series({'Mean': corrs.mean(), "S.D.": corrs.std(), "Normalised S.D.": corrs.mean() / corrs.std()})

fig.tight_layout()

<Figure size 504x216 with 2 Axes>

#### 2.4.5.d Calculate the covariance matrix, cov(R) using a rolling window of 22 days. Comment on the magnitude and stability of the covariance matrix.

We have regressed a 2-factor model with risk premiums $R_m$ and $R_s$ for the market return and size of the market. We now aim to see how these risk premiums are correlated for each trading month across the time-series. This result confirms the previous conclusion that the two-factor model was not adequately descriptive of returns. Plotting the determinant of the covariance matrices (i.e.~their maximum variance) shows a highly unstable signal whose determinant is close to 0 at many times, and superimposing the inter-day percentage change results in large spikes. This shows that $R_m$ and $R_s$ change rapidly and unpredictably with respect to each other, and that there is a lack of a formal relationship between the two.

In [25]:
factors = pd.DataFrame({ "Rm": Rm, "Rs": Rs })
R_matrices = []

for i in factors.index[21:]:
    R_matrices.append(np.cov(factors[:i][-22:].transpose()))

R_matrices = np.array(R_matrices)
mag = pd.Series(index=factors.index[21:])
change = pd.Series(index=factors.index[21:])

for i in range(R_matrices.shape[0]-1):
    curr, prev = (R_matrices[i+1], R_matrices[i])
    mag.iloc[i] = np.linalg.det(curr)
    change.iloc[i] = 100 * np.mean(abs((curr - prev)/prev))

fig, ax1 = plt.subplots(1)
fig.suptitle("Rolling Factor Covariance Analysis", fontsize=14, fontweight="bold")
fig.set_size_inches(5,3)
mag.plot(ax=ax1)
plt.ylabel('Cov(R) Determinant', color='black')
change.plot(ax=ax1.twinx(), style='r-')
plt.ylabel('Cov(R) Average Percentage Change (%)', color='r')
plt.grid()

<Figure size 360x216 with 2 Axes>

### 2.4.5.e. Estimate the covariance matrix of these specific returns, cov(E). Perform PCA on the covariance matrix, find the percentage of the variance explained by the first principal component, and comment on the result.

It has been established that the 2-factor model is inadequate to describe the returns of the market in this time series, and that the specific return $\epsilon$ is highly correlated to the market returns and thus still contains most of the information behind our mysterious market price movements. A quantitative method of exploring this further is by using principal component analysis (PCA).

PCA is a dimensionality reduction technique that uses eigendecomposition of a covariance matrix to determine which eigenvectors point into the direction of the largest variance of the data. This aligns with a key concept of information theory: that the information contained by a random variable is tied to its variance. In this case, the eigenvector with the largest eigenvalue of our correlation matrix of special returns is therefore the dimension which best explains the fluctuation in market prices!

The eigenvectors have no explicit physical interpretation, but represent an abstract direction which best explains the variance of the data. Often, analysts try to find physical meaning behind these abstract directions to better understand what factors affect the phenomenon they are investigating.

In this case, the first (largest) principal component explained 7.35% of the variance (information) of the specific return. The plot below shows that the first 75 principal components are required to explain 90.22% of the variance in the returns, which further explains why the 2-factor model failed, since by comparison, even the first 2 principal components accounted for only 12.37% of the variance.

Since the two-factor model failed to explain the returns of the market in terms of the market return and the size of the asset in the market, we can safely conclude that neither of these metrics are represented by these principal components, and that the factors affecting market returns lie elsewhere.

In [26]:
# This function returns eigenvalues returned in ascending magnitude
eigvals, _ = np.linalg.eigh(e.astype(float).cov())

fig, ax = plt.subplots()
fig.set_size_inches(5,3)
fig.suptitle('Eigenvalues Ordered by Variance Contribution', fontsize=14, fontweight="bold")
# Reverse the list so it plots ascending eigenvals
ax.plot(eigvals[::-1] / sum(eigvals) * 100)
ax.set_ylabel('% Variance')
ax.set_xlabel('Eigenvalue Number')
ax.grid()

cum_exp_var = np.cumsum(eigvals[::-1]/sum(eigvals)*100)
ax.twinx().plot(cum_exp_var, color='r')
plt.ylabel('Cumulative Explained Variance (%)', color='r')

fig.tight_layout()

print('% of Variance explained by the 1st Principal Component:', round(cum_exp_var[0],2), '%')
print('% of Variance explained up to the 2nd Principal Component:', round(cum_exp_var[1],2), '%')
print('% of Variance explained up to the 76th Principal Component:', round(cum_exp_var[75],2), '%')

% of Variance explained by the 1st Principal Component: 7.35 %
% of Variance explained up to the 2nd Principal Component: 12.37 %
% of Variance explained up to the 76th Principal Component: 90.22 %


<Figure size 360x216 with 2 Axes>

# 3. Adaptive Minimum-variance portfolio Optimisation

- [ ] Center and label all equations
- [ ] Calculate and compare theoretical variance

Mean-variance portfolio theory is based on the thought that the risk of a portfolio is characterised by the variance of its underlying securities. An optimal investor would therefore want to achieve a desired return on investment while bearing the lowest possible risk: therefore constructing a portfolio that lies on the lowest boundary on a mean-variance plot. 

In a given market of assets, each security can be characterised by its return $r_i$ and its variance $\sigma^2_i$. The optimal investor invests in assets by allocating a portion of capital to each asset. Therefore, the portfolio can be characterised purely by its weights in matrix form:

\begin{equation}
    \textbf{w} = \begin{vmatrix}
        w_1 \\
        w_2 \\
        ... \\
        w_n \\
    \end{vmatrix}
\end{equation}

The return of the portfolio is therefore simply the matrix product of the weights with the vector of asset returns $\textbf{r}_p = \textbf{w}^T\textbf{r}$, and it can be shown that the resulting variance of the portfolio is $\sigma_p^2 = \textbf{w}^T\textbf{C}\textbf{w}$. 

## 3.1 Constructing an optimal minimum-variance portfolio
Therefore, we can formulate the optimal portfolio as an optimisation problem. Note that in the following formulation, short selling is allowed, and therefore weights can be negative:

\begin{equation}
    \textbf{w}_{opt} = argmin_{\textbf{w}} \frac{1}{2} \textbf{w}^T\textbf{C}\textbf{w} \\
    \text{ s.t. } \textbf{w}^T \textbf{1} = 1
\end{equation}

We introduce a coefficient of 0.5 to the objective out of convenience, for the problem can be solved by the method of Lagrange multipliers, yielding the following Lagrangian:

\begin{equation}
    L = \frac{1}{2} \textbf{w}^T\textbf{C}\textbf{w} - \lambda (\textbf{w}^T \textbf{1} - 1)
\end{equation}

Now proceeding to differentiate it with respect to $\textbf{w}$ and the Lagrange multiplier $\lambda$. Notice that the aforementioned coefficient is multiplied away due to the derivative:

\begin{equation}
        \frac{dL}{d\textbf{w}} = \textbf{C}\textbf{w} - \lambda \textbf{1} = 0 
    \Rightarrow
    \textbf{w} = \lambda \textbf{C}^{-1} \textbf{1}
    \\
    \frac{dL}{d\lambda} = \textbf{w}^T \textbf{1} - 1 = 0 \Rightarrow \textbf{w}^T \textbf{1} = 1
\end{equation}

We now have a system of equations which we can solve vectorially to obtain the optimal weights $w_{opt}$:

\begin{equation}
    \textbf{w}^T \textbf{1} = (\lambda \textbf{C}^{-1} \textbf{1})^T \textbf{1} 
    = \lambda \textbf{1}^T \textbf{C}^{-1^T} \textbf{1}
    \Rightarrow
    \lambda = \frac{1}{\textbf{1}^T \textbf{C}^{-1^T} \textbf{1}}
\\
    \textbf{w}_{opt} = \lambda \textbf{C}^{-1} \textbf{1} 
    = \frac{1}{\textbf{1}^T \textbf{C}^{-1^T} \textbf{1}} \textbf{C}^{-1} \textbf{1}
\end{equation}
    
The theoretical variance of the minimum-variance portfolio is therefore:

\begin{equation}
    \sigma_p^2 = \textbf{w}_{opt}^T\textbf{C}\textbf{w}_{opt} 
    = \frac{1}{(\textbf{1}^T \textbf{C}^{-1^T} \textbf{1})^2} 
    (\textbf{C}^{-1} \textbf{1})^T \textbf{C} (\textbf{C}^{-1} \textbf{1})
    = \frac{1}{(\textbf{1}^T \textbf{C}^{-1^T} \textbf{1})^2} 
    \textbf{1}^T \textbf{C}^{-1^T} \textbf{1}
    = \frac{1}{\textbf{1}^T \textbf{C}^{-1^T} \textbf{1}} = \lambda
\end{equation}

## 3.2 Back-testing a minimum-variance strategy

Using the last 10 stocks of the dataset of 157 European companies from earlier, we now aim to benchmark the minimum-variance strategy against a naive equal weight strategy. The portfolio weights are constructed on the first chronological half of the data, and we will test its performance on the other half.

In [27]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import statsmodels.api as sm
from sklearn import linear_model
from scipy.stats import pearsonr
from sklearn.decomposition import PCA
from scipy.optimize import minimize

# Basic pre-processing
data = pd.read_csv('data/q2/fsp_case_31_BSD.csv', index_col=0, header=[0 ,1])
returns = data['ret'].copy().fillna(0)
returns.index = pd.to_datetime(returns.index)
returns = returns.sort_index()
returns = returns.iloc[:,-10:]

# Split into training and testing sets
returns_train = returns.iloc[:int(returns.shape[0]/2), :]
returns_test = returns.iloc[int(returns.shape[0]/2):, :]

### 3.2.1 Equal weights portfolio

From the results of the equally-weighted portfolio shown below, two points are apparent. These 10 stocks are generally uptrending during the training split, and declining on the test split. Furthermore, since these stocks were selected arbitrarily, he resulting portfolio of 10 stocks may not be well-diversified or sensible.

In [28]:
"""
This function takes the returns of a portfolio and evaluates its performance.
The input expected is the weights to be element-wise multiplied to each asset's return.
"""
def evaluate_weights(portfolio, tvar, name, plot=True):
    if plot:
        fig, (ax1, ax2) = plt.subplots(2,1)
        fig.suptitle(f'{name} Performance Analysis', fontsize=12, fontweight="bold")
        fig.set_size_inches(5,3)
        portfolio.plot(grid=True, title='Daily Return', ax=ax1).set_ylabel('Returns')
        portfolio.cumsum().plot(grid=True, title='Cumulative Daily Return', ax=ax2).set_ylabel('Returns')
        plt.tight_layout()

    performance = pd.Series()
    performance['Mean Return']=portfolio.mean()
    performance['Cumulative Return']=portfolio.cumsum()[-1]
    performance['Variance']=portfolio.std()**2
    performance['Theoretical Variance'] = tvar
    performance['Sharpe']=portfolio.mean()/portfolio.std()**2

    return performance

# For the equally-weighted portfolio, we can simply take the mean returns across all assets.
naive_portfolio_train = returns_train.mean(axis=1)
naive_portfolio_test = returns_test.mean(axis=1)

# C = returns_train.cov()
# w = np.full(10, 0.1)
# equal_tvar_train = w.T.dot(C).dot(w)

# C = returns_test.cov()
# equal_tvar_test = w.T.dot(C).dot(w)

eq_performance_train = evaluate_weights(naive_portfolio_train, '-', "Equally-weighted (Training)")
eq_performance_test = evaluate_weights(naive_portfolio_test, '-', "Equally-weighted (Test)")

<Figure size 360x216 with 2 Axes>

<Figure size 360x216 with 2 Axes>

### 3.2.2 Minimum-Variance portfolio

Calculating the minimum-variance portfolio is a simple matter of linear algebra, following the derivation we achieved before:

In [29]:
"""
This implements the derivation for optimal weights that we found earlier, returning
the weights as a 1-D vector.

As an exercise, we calculate and return the theoretical variance, although it should 
equal the variance of the returns achieved on the data these weights were trained on.
"""
def find_weights(returns):
    ones = np.ones(returns.shape[1])
    C = returns.cov()
    tvar_lambda = 1/(ones.T.dot(np.linalg.inv(C).T).dot(ones))
    Lambda = 1/(ones.T.dot(np.linalg.inv(C).T).dot(ones))
    w_opt = Lambda*(np.linalg.inv(C).dot(ones))
    return w_opt.reshape(-1), tvar_lambda

w_opt, tvar = find_weights(returns_train)

# Multiply the weights element-wise, then sum over all assets.
MV_portfolio = (returns_train * w_opt).sum(1)
mv_train_performance = evaluate_weights(MV_portfolio, tvar, "M.V. (Train)")

<Figure size 360x216 with 2 Axes>

While results initially look ideal with a 25% return over the year, these results are purely theoretical as calculating the optimal weights requires the availability of future data, which is obviously impossible. Applying the weights to the next investment period yields the following result:

In [30]:
MV_test_portfolio = (returns_test * w_opt).sum(1)
test_mv = evaluate_weights(MV_test_portfolio, tvar, "M.V. (Test)")

results = pd.DataFrame({
    "Equal weights": eq_performance_test,
    "MV portfolio (Train)": mv_train_performance,
    "MV portfolio (Test)": test_mv
})
results.iloc[1:4, :]

Equal weights  MV portfolio (Train)  MV portfolio (Test)
Cumulative Return        -0.123503              0.249062            -0.117582
Variance                  0.000079              0.000029             0.000082
Theoretical Variance             -              0.000029             0.000029

<Figure size 360x216 with 2 Axes>

The optimal weights perform just 0.5% better than the equally-weighted portfolio over the period, which reveals the fallacy in this strategy. Mean-variance portfolio theory relies on the underlying data (mean, variance and correlation of the assets) being correct. Using historical data to estimate empirical estimates as we have done here is often flawed. Not enough data exists to have the resulting statistics be statistically reliable. Furthermore, market conditions change quickly, and are uncorrelated to historical data, so the optimal set of calculated weights very quickly become irrelevant. This is further confirmed by comparing the theoretical variance from the returns on training data, which varies greatly from the actual variance attained using the optimal weights on the test set. Using the optimal weights incurred a variance of 0.000082, almost 3 times that of our theoretical variance.

### 3.2.3 Adaptive Minimum-variance portfolio

Since we established that market conditions change too quickly for previously calculated weights to be useful over time, what we could do instead is craft an adaptive min-variance portfolio that calculates new weights every day based on a rolling window of previous days' data. There is no need for a training and test split in this case. Instead, we need to find the optimal rolling window size, which we determine by using a brute force search.

In [31]:
n_months = list(range(1,12))
window_sizes = [22 * month for month in n_months]
amv_results = pd.DataFrame(columns=window_sizes)

for window in window_sizes:
    amv_port = pd.Series()

    for day in returns_test.index[window:]:
        w_opt, _ = find_weights(returns_test[:day][-window-1:-1])
        amv_port[day] = sum(returns_test.loc[day] * w_opt)
    amv_results[window] = evaluate_weights(amv_port, "-", "AMV", plot=False)

fig, (ax1, ax2) = plt.subplots(2,1)
fig.suptitle('Returns and Variance by Window Size', fontsize=14, fontweight="bold")
fig.set_size_inches(5,4)
ax1.bar(n_months, amv_results.iloc[1])
ax1.set_title('Cumulative Returns')
ax1.set_xlabel('Window Size (Months)')
ax1.set_ylabel('Cumulative Returns')
ax1.grid()

ax2.bar(n_months, amv_results.iloc[2])
ax2.set_title('Variance')
ax2.set_xlabel('Window Size (Months)')
ax2.set_ylabel('Variance')
ax2.grid()

fig.tight_layout()

opt_months = np.argmax(amv_results.iloc[1]) + 1
results["Adaptive MV"] = amv_results.loc[:, opt_months * 22]

<Figure size 360x288 with 2 Axes>

The optimal portfolio is achieved with a window size of 2 months, yielding a 10.6% cumulative return. For a final comparison, the results of the whole market portfolio in this test period are also added. The adaptive minimum-variance portfolio well-outperforms all the other strategies, while not incurring significantly more risk (measured in variance magnitude) and in fact having less risk than the equally-weighted portfolio. While this may initially sound prospective, the transaction costs that would be incurred in rebalancing the portfolio every day would likely negate our profits even at the optimal 10.6% cumulative return.

In [32]:
mport_data = data[['ret', 'mcap']].copy().fillna(0)
mport_data.index = pd.to_datetime(mport_data.index)
mport_data = mport_data.sort_index()
mport_data = mport_data.iloc[int(returns.shape[0]/2):, :]

market_port_returns = mport_data['ret'] * mport_data['mcap']
total_market_caps = mport_data['mcap'].sum(axis=1)            # Daily total market values
market_port_returns = market_port_returns.sum(axis=1).divide(total_market_caps)  # Sum across companies and divide by total market cap
results["Market Portfolio"] = evaluate_weights(market_port_returns, "-", "Market", plot=False)
results

Equal weights  MV portfolio (Train)  MV portfolio (Test)  \
Mean Return              -0.000473              0.000958            -0.000451   
Cumulative Return        -0.123503              0.249062            -0.117582   
Variance                  0.000079              0.000029             0.000082   
Theoretical Variance             -              0.000029             0.000029   
Sharpe                   -5.964545             33.475039            -5.499329   

                     Adaptive MV Market Portfolio  
Mean Return              0.00049        -0.000156  
Cumulative Return       0.106409        -0.040606  
Variance                0.000066         0.000059  
Theoretical Variance           -                -  
Sharpe                  7.417396        -2.632947

In this example, a sample covariance matrix (SCM) is obtained using a range of previous days' returns. However, SCMs are highly affected by outliers and are often unbiased and inefficient estimators, especially using only a small volume (44 samples, in the case of 2 trading months) of data. Furthermore, important factors such as investor sentiment and market conditions change too rapidly for large amounts of historical data to be relevant. One method of achieving a more accurace sample covariance matrix is to therefore use more data, but apply exponential weight decay to make the recent returns have more influence than chronologically older returns. This way, we reduce the impact of outlying data, but also attempt to place a greater emphasis on recent market events.

# 4. Robust Statistics and Non Linear Methods

## 4.1 Data Import and Exploratory Data Analysis

### 4.1.1. Import AAPL.csv, IBM.csv, JPM.csv and DJI.csv into separate pandas.DataFrames, and set the date as the index column. For each stock and for each column, generate the key descriptive statistics (e.g. mean, median, stddev, etc.) that summarize the distribution of the dataset. Lastly, using the adj. close column for each stock, compute the 1-day returns and add them to their corresponding dataframe as a new column.

In [33]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings('ignore')

# Import, re-index and sort by date
DJI = pd.read_csv("data/q4/DJI.csv").set_index("Date").sort_index()
AAPL = pd.read_csv("data/q4/AAPL.csv").set_index("Date").sort_index()
IBM = pd.read_csv("data/q4/IBM.csv").set_index("Date").sort_index()
JPM = pd.read_csv("data/q4/JPM.csv").set_index("Date").sort_index()

DJI.index = pd.to_datetime(DJI.index)
AAPL.index = pd.to_datetime(AAPL.index)
IBM.index = pd.to_datetime(IBM.index)
JPM.index = pd.to_datetime(JPM.index)

# Sanity check for null values and same shape
nan_count = (AAPL.isna().sum() + IBM.isna().sum() + JPM.isna().sum() + DJI.isna().sum()).sum()
same_shape = AAPL.shape == IBM.shape == JPM.shape == DJI.shape

if not nan_count and same_shape:
    print(f"Total {len(AAPL.index)} entries")

AAPL.head(3)        # Visualise data briefly

Total 251 entries


Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-03-16  178.649994  179.119995  177.619995  178.020004  175.349915   
2018-03-19  177.320007  177.470001  173.660004  175.300003  172.670731   
2018-03-20  175.240005  176.800003  174.940002  175.240005  172.611618   

              Volume  
Date                  
2018-03-16  39404700  
2018-03-19  33446800  
2018-03-20  19649400

After importing and sanity-checking the data, we confirm that we have a clean data set of 251 entries, which is about one trading year. Key descriptive statistics are conventionally defined as the statistics up to the 4th moment of the data, and so we generate the mean, median, standard deviation, skewness and kurtosis of each column of every stock.

In [34]:
key_stats = ['Median', 'Mean', 'S.D.', 'Skew', 'Kurtosis']

stock_stats = pd.DataFrame(index=key_stats, columns=DJI.columns)

all_stats = {
    "DJI": stock_stats.copy(),
    "AAPL": stock_stats.copy(),
    "IBM": stock_stats.copy(),
    "JPM": stock_stats.copy()
    }

stock_names = [ "DJI", "AAPL", "IBM", "JPM" ]
all_stocks = [ DJI, AAPL, IBM, JPM ]

for i, stock in enumerate(all_stocks):
    for col in stock.columns:
        data = stock[col]
        all_stats[stock_names[i]][col]['Median'] = data.median()
        all_stats[stock_names[i]][col]['Mean'] = data.mean()
        all_stats[stock_names[i]][col]['S.D.'] = data.std()
        all_stats[stock_names[i]][col]['Skew'] = data.skew()
        all_stats[stock_names[i]][col]['Kurtosis'] = data.kurtosis()
    stock['Returns'] = stock['Adj Close'].pct_change()

for name in stock_names:
    print("\n", name)
    print(all_stats[name])



 DJI
                  Open          High           Low         Close  \
Median    25025.580078  25124.099609  24883.039063  25044.289063   
Mean      25001.257268  25142.041965  24846.002226  24999.153581   
S.D.        858.834708    815.203959    903.302186    859.132105   
Skew         -0.372127     -0.239367     -0.456447     -0.380147   
Kurtosis      0.485736      0.118153      0.557592      0.400668   

             Adj Close            Volume  
Median    25044.289063       313790000.0  
Mean      24999.153581  332889442.231076  
S.D.        859.132105    94078038.14115  
Skew         -0.380147           1.73956  
Kurtosis      0.400668          5.857581  

 AAPL
                Open        High         Low       Close   Adj Close  \
Median    186.289993  187.399994  184.940002  186.119995  184.351776   
Mean      187.686694  189.561753  185.823705  187.711953  186.174273   
S.D.       22.145621   22.281577   22.008797   22.160721   21.904664   
Skew        0.259917    0.300385

### 4.1.2. Plot the histogram and probability density function of the adj. close and 1-day returns. Comment on the difference, if any, between the pdf of the the adj. close and the returns.

To estimate the distributions, we use the `.plot.kde` function, which performs kernel density estimation in order to fit a PDF using gaussian kernels. The resulting PDF is much better fitted to the returns than to prices, as we know from the results of Section 1 that returns are normally distributed in the short term, but prices are not. There is one exception to this rule: the prices of the DJI appear somewhat normally distributed, which could be attributed to the central limit theorem. Since the DJI is a weighted aggregation of 30 large stocks, it is a sum of many more independent random variables than any single stock, and therefore its prices appear to be normally distributed. However, since prices in general are less likely to be normally distributed, using robust statistics such as the median and median absolute deviation (MAD) might be more stable than using mean and standard deviation.

In [35]:
fig, axes = plt.subplots(2, 4)
fig.suptitle('Histogram and PDF of Daily Adjusted Closes and Returns', fontsize=14, fontweight="bold")
fig.set_size_inches(10,5)

for i, stock in enumerate(stock_names):
    axes[0][i].set_title(f'{stock} Adj Close')
    axes[1][i].set_title(f'{stock} Returns')

    close_returns = all_stocks[i][["Adj Close", "Returns"]].dropna()
    tmp = axes[0][i].hist(close_returns["Adj Close"], bins=30, color='b')
    close_returns['Adj Close'].plot.kde(ax=axes[0][i].twinx(), color='r', grid=True)
    axes[1][i].hist(close_returns["Returns"], bins=30, color='b')
    close_returns['Returns'].plot.kde(ax=axes[1][i].twinx(), color='r', grid=True)

fig.tight_layout()

<Figure size 720x360 with 16 Axes>

### 4.1.3. For each stock, plot the adj. close, the associated rolling mean (using a 5-day window), and the ±1.5 × standard deviations relative to the rolling mean. In a separate figure, repeat the steps above using the rolling median (using a 5-day window) and ±1.5× median absolute deviation relative to the rolling median. Comment on the difference, if any, between the two figures.

Without outliers, the z-score ranges between the two methods are not meaningfully discernable from a visual standpoint. Furthermore, because only a rolling window of 5 samples is used, the standard deviation (or MAD, which we use in the median method) is very small and the Z-score ranges are therefore very tight.

In [36]:
from statsmodels.robust.scale import mad

def outlier_detection(stock, name, ax, mean=True):
    close_returns = stock["Adj Close"]
    ax.plot(close_returns, color='black')
    
    rolling = close_returns.rolling(5)
    rolling_stat = rolling.mean() if mean else rolling.median()
    upper_std = rolling_stat + 1.5 * (rolling.std() if mean else rolling.apply(mad))
    lower_std = rolling_stat - 1.5 * (rolling.std() if mean else rolling.apply(mad))

    ax.plot(rolling_stat, color='red')
    ax.plot(upper_std, 'b:', alpha=0.2)
    ax.plot(lower_std, 'b:', alpha=0.2)
    ax.fill_between(rolling_stat.index, upper_std, lower_std, color='b', alpha=0.2)
    ax.grid()

    method = "Mean" if mean else "Median"
    ax.set_title(f"{method} Z-score range: {name}")
    return len(close_returns[close_returns>upper_std])+len(close_returns[close_returns<lower_std])

def outlier_comparison(stocks):
    fig, axes = plt.subplots(4, 2)
    fig.suptitle('Z-score Outlier Detection Comparison', fontsize=16, fontweight="bold")
    fig.set_size_inches(12,8)
    mean_outliers = pd.Series(index=stock_names)
    med_outliers = pd.Series(index=stock_names)

    for i,stock in enumerate(stock_names):
        mean_outliers[stock] = outlier_detection(stocks[stock_names.index(stock)], stock, axes[i][0])
        med_outliers[stock] = outlier_detection(stocks[stock_names.index(stock)], stock, axes[i][1], mean=False)

    fig.tight_layout()
    return pd.DataFrame({"Mean Outliers": mean_outliers, "Median Outliers": med_outliers})

normal_outliers = outlier_comparison(all_stocks)

<Figure size 864x576 with 8 Axes>

### 4.1.4. Introduce outlier points for the adj. close in the four dates {2018-05-14, 2018-09-14, 2018-12-14, 2019-01-14} with a value equal to 1.2 × the maximum value of the column. Comment on the impact of the outlier points in Part 3.

With the introduction of extreme outliers, we can visually observe from the plots below that the Z-score range is highly affected in the case of mean outlier detection, resulting in previously acceptable data points being classified as outliers. The median method performs much better in this respect, as the acceptable Z-score range is largely unchanged in the regions with outliers.

In [37]:
outlier_dates = ['2018-05-14', '2018-09-14', '2018-12-14', '2019-01-14']
stock_outlier_copies = [ DJI.copy(deep=True), AAPL.copy(deep=True), IBM.copy(deep=True), JPM.copy(deep=True) ]

for stock in stock_outlier_copies:
    max_val = stock["Adj Close"].max()
    for date in outlier_dates:
        stock["Adj Close"][date] = 1.2 * max_val

corrupted_outliers = outlier_comparison(stock_outlier_copies)
# (corrupted_outliers - normal_outliers - 4).rename(columns={"Mean Outliers": "Additional outliers (mean)", "Median Outliers": "Additional outliers (median)"})

<Figure size 864x576 with 8 Axes>

### 4.1.5. Generate a box plot for the adj. close for each stock, describe the information the box plot conveys and elaborate on any other observations you may have.

A box plot is a compact representation of the median, interquartile range (IQR) and min/max values in a data series. In the case of the `matplotlib` implementation below, the orange line represents the median, and the box represents the upper and lower bounds of the IQR (75th and 25th percentile). The "whiskers" on the outside of the box represent the minimum and maximum values. Outliers in this case are defined as points which lie outside of 1.5 times the IQR, and are plotted as small bubbles outside the whiskers' range.

Taking the box plot for IBM as an extreme example, we see that the median is highly skewed towards the 75th percentile, and the data is thus highly "compressed" between the 50th and 75th quartile, resulting in very asymmetric ranges in each quartile.

In [38]:
fig, axes = plt.subplots(1, 4)
fig.suptitle('Box Plots for 4 Stocks', fontsize=16, fontweight="bold")
fig.set_size_inches(6,3)
fig.tight_layout()

for i, stock in enumerate(all_stocks):
    ax = axes[i]
    ax.grid()
    ax.boxplot(stock["Adj Close"])
    ax.set_title(stock_names[i])

<Figure size 432x216 with 4 Axes>

## 4.2 Robust Estimators

### 4.2.1 Custom Robust Estimators
In this section, we will explore the use of robust estimators, which aim to outperform classical statistical methods in the presence of outliers. We will create robust estimations of the median, interquartile range (IQR) and median absolute deviation (MAD), which are implemented as follows:

In [39]:
def robust_median(data):
    sorted_vals = data.sort_values() 
    return sorted_vals[round(len(sorted_vals)/2)]

def robust_IQR(data):
    sorted_vals = data.sort_values()
    percentile_25 = sorted_vals[round(len(sorted_vals)/4)]
    percentile_75 = sorted_vals[round(len(sorted_vals)/4*3)]
    return percentile_75-percentile_25

def robust_MAD(data):
    median = robust_median(data)
    return robust_median(abs(data - median)) # compute the median of deviations

### 4.2.2. Complexity Analysis

All the calculations involve sorting, which is typically implemented in $O(nlog(n))$, where $n$ is the number of elements involved in the sort. However, in this particular case, pandas actually uses quicksort under the hood, and thus we have a best-case sorting time of $O(log(n))$, and a worst-case of $O(n^2)$. All index lookups are assumed to be efficiently implemented with hash-tables, and so we assume a constant complexity of O(1).

Calculating the median is a matter of sorting and a single index lookup, which in the best case is $O(log(n) + 1) = O(log(n))$ and in the worst case is $O(n^2 + 1) = O(n^2)$.

For the IQR, we sort the values, then find the values at the 25th and 75th percentile, which are simply index lookups as before. This is hence slightly more expensive than the median estimator, but only by a constant factor and thus ends up similarly with the same best and worst case of $O(log(n))$ and $O(n^2)$ respectively.

The median absolute deviation first requires finding the median. Then, it computes the deviation from the median for all $n$ data which has complexity $O(n)$. Finally, the median of all deviations is found to be the MAD which is another operation of complexity $O(nlog(n))$. Overall, MAD is the estimator with the highest computational cost: $O(2*log(n) + n)$

In comparison, finding the mean requires a single access to every value, resulting in an $O(n)$ complexity, and the standard deviation requires first finding the mean and then taking the expectation of the difference across every point, which is $O(2n) \approx O(n)$

### 4.2.3. Breakdown Points

The finite sample breakdown point of an estimator is defined as the fraction of data (of a sample size $n$) which can be arbitrarily changed without affecting the estimator's quality significantly, and therefore is a vague measure of its robustness. The asymptotic breakdown point is the finite sample breakdown points as $n$ tends to infinity.

The median estimator has a breakdown point of 0.5, since up to $\frac{(0.5n-1)}{n}$ values can be contaminated and the median would still remain unchanged. Similarly, the IQR estimator has a breakdown point of 0.25 since it splits the data array into 4 parts instead of 2 parts. The median-absolute-deviation has the same breakdown point as the median of 0.5, since it computes the median and then finds the median of absolute deviation from the median.

## 4.3 Robust and Ordinary Least Squares Regression


Previously, OLS regression was used to regress values for the two-factor model in the experiment on Arbitrage Pricing Theory. This section explores robust regression against least-squared regression in the presence of data that is contaminated by outliers. 

The Dow Jones Industrial Average (DJI) tracks 30 large-cap stocks in the US market, of which Apple, IBM and J.P. Morgan are all included. There might therefore be a two-way correlation between the index and any of its underlying stocks, as investors might tie a stock's presence in the DJIA as a sign of it being a healthy presence in the market of assets.

To investigate this correlation, we regress the 1-day returns of each individual stock against the same-day return for DJI using OLS and Huber regression, and seek to compare the results.

### 4.3.1 Ordinary Least-squares Regression

We seek to solve the regression of the form 

\begin{equation}
    \textbf{r} = \textbf{Ax} + \textbf{e}
\end{equation}

where we want to obtain the coefficients $\textbf{x}$ which will relate the returns of the stock $\textbf{r}$ to the returns of the DJIA ($\textbf{A}$) along with an error term $\textbf{e}$. OLS regression seeks to minimise magnitude of the mean squared error $||\textbf{e}||^2=||\textbf{r} - \textbf{Ax} ||^2$. This regression method is therefore highly sensitive to outliers since the error that it tries to minimise will be very large in the case of an outlying point, and the quality of the underlying model thus suffers significantly.

In [40]:
from sklearn import linear_model
from sklearn.metrics import mean_squared_error

# Re-declare these variables for clarity, gather 1-day returns
stock_names = [ "DJI", "AAPL", "IBM", "JPM" ]
returns = pd.DataFrame(columns=stock_names)
for i, stock in enumerate(stock_names):
    returns[stock] = all_stocks[i]["Returns"].dropna()

# Ordinary least squares regression
ols_regressor = linear_model.LinearRegression()

def regress_model(regressor, method, returns):
    results = pd.DataFrame(columns=stock_names, index=['alpha', 'beta', 'mse'])

    fig, axes = plt.subplots(3,1)
    fig.suptitle(f'{method} Regression against DJI', fontsize=14, fontweight="bold")
    fig.set_size_inches(6,4)
    fig.tight_layout()

    for i,stock in enumerate(stock_names[1:]):
        r = returns[stock].copy().values.reshape(-1,1)
        A = returns['DJI'].copy().values.reshape(-1,1)
        regressor.fit(A, r)
        results[stock]['alpha'] = float(regressor.intercept_)
        results[stock]['beta'] = float(regressor.coef_)
            
        ax = axes[i]
        pred = regressor.predict(A)
        results[stock]['mse'] = mean_squared_error(r, pred)
        ax.plot(returns[stock].index, r)
        ax.plot(returns[stock].index, pred)
        ax.legend(['r','pred'])
        ax.grid()
        ax.set_title(stock)
        ax.set_ylabel('Returns')

    return results

regress_model(ols_regressor, "OLS", returns)

DJI      AAPL       IBM       JPM
alpha  NaN  0.000165 -0.000441 -0.000316
beta   NaN   1.32558  0.960092  0.931408
mse    NaN   0.00018   0.00014  0.000076

<Figure size 432x288 with 3 Axes>

### 4.3.2 Huber Regression

Huber regression improves upon the OLS method by varying the magnitude of its error term using a threshold value $\epsilon$. For $\frac{||\textbf{r} - \textbf{Ax} ||}{\sigma} < \epsilon$, it minimises the squared error and for $\frac{||\textbf{r} - \textbf{Ax} ||}{\sigma} > \epsilon$, it minimises the absolute error.  This reduces the impact of outliers by only correcting on a linear scale rather than quadratic for large errors. This depends on careful selection of the threshold value, and is still a relatively naive method, but produces better results as shown below.

In [41]:
# Huber regression
huber_regressor = linear_model.HuberRegressor(epsilon=1.0)
regress_model(huber_regressor, "Huber", returns)

DJI      AAPL       IBM       JPM
alpha  NaN -0.000149 -0.000628 -0.000485
beta   NaN  1.297928  1.012351  0.909187
mse    NaN   0.00018  0.000141  0.000076

<Figure size 432x288 with 3 Axes>

### 4.3.3 Comparison of Performance with Outliers

To compare the performance of both regressors, we take the difference of the mean squared error of the predicted signal against the ground truth for both regressors. Interestingly, the Huber regressor has a higher MSE across all stocks. However, it is visually noticeable that the Huber regressor's prediction signal does not fit to the outlying data points as much as the OLS regressor, which we expect.

In [42]:
corrupted_returns = pd.DataFrame(columns=stock_names)
for i, stock in enumerate(stock_names):
    corrupted_returns[stock] = stock_outlier_copies[i]["Adj Close"].pct_change().dropna()

ols_regressor = linear_model.LinearRegression()
huber_regressor = linear_model.HuberRegressor(epsilon=1.0)

regress_model(ols_regressor, "OLS", corrupted_returns) - regress_model(huber_regressor, "Huber", corrupted_returns)

DJI      AAPL       IBM       JPM
alpha  NaN  0.001091   0.00071  0.001049
beta   NaN  0.193755  0.195745  0.002105
mse    NaN -0.000093 -0.000094 -0.000001

<Figure size 432x288 with 3 Axes>

<Figure size 432x288 with 3 Axes>

## 4.4 Robust Trading Strategies

The moving average crossover strategy is an example of a simple trading strategy based on mean reversion:

- Buy X shares of a stock when its 20-day MA > 50-day MA
- Sell X shares of the stock when its 20-day MA < 50-day MA

Since this strategy uses averages to come up with a trading strategy, there are ways to increase its robustness to outliers as we have done in the previous sections. 

### 4.4.1 Moving Average Crossover (Mean)

Beginning with the mean crossover strategy, we calculate the required moving average signals and plot them all in the same graph. The sign of the difference of both moving averages is the resulting trading signal: we should go "long" (buy) on the stock if it is positive, and "short"(sell) if it is negative. After determining the trading signal, identify the crossover points and shade in an appropriate colour based on the signal between points.

In [43]:
stock_names = [ "DJI", "AAPL", "IBM", "JPM" ]

def eval_ma_strategy(stock, ax, mean=True):
    closing_price = all_stocks[stock_names.index(stock)]["Adj Close"]
    closing_price_outliers = closing_price.copy()

    max_val = 1.2 * max(closing_price)
    for idx in [i for i in range(0,250,50)]:
        closing_price_outliers[idx] = max_val
    
    cumulative_returns = []

    for k,prices in enumerate([closing_price, closing_price_outliers]):
        MA_20 = prices.rolling(20).mean() if mean else prices.rolling(20).median()
        MA_50 = prices.rolling(50).mean() if mean else prices.rolling(50).median()
        MA_regions = np.sign((MA_20-MA_50).dropna()) # Buy if +ve, sell if -ve

        # Define a starting point, since the calculation using averages results in nulls
        start = MA_regions.index[0]

        prices[start:].plot(color='black', alpha=0.5, ax=ax[k])
        MA_20[start:].plot(style='b-', ax=ax[k], label="MA20")
        MA_50[start:].plot(style='r-', ax=ax[k], label="MA50")

        crossover_points = []

        # Create an array of crossover points
        for i,point in enumerate(MA_regions.index[:-1]):
            # If the sign of the region changes between two points, squaring their
            # sum results in a number less than 2
            if i == 0 or i == len(MA_regions.index[:-1])-1 or (MA_regions[point] + MA_regions.iloc[i+1])**2 < 2:
                crossover_points.append((point, MA_regions.iloc[i+1]))

        for i, pointAndSign in enumerate(crossover_points[:-1]):
            point, sign = pointAndSign
            color = 'g' if sign > 0 else 'r'
            ax[k].axvspan(point, crossover_points[i+1][0], color=color, alpha=0.3, lw=0)

        outliers = "(outliers)" if k == 1 else ""
        ax[k].set_title(f'{stock} {outliers}')
        ax[k].legend()

        returns = np.log(prices[MA_regions.index[0]:]).diff(1)
        returns *= MA_regions
        c_returns = returns.cumsum()
        cumulative_returns.append(c_returns[-1])

    return cumulative_returns

From plotting the trading signal below and calculating the cumulative sum, it is clear that the addition of outlying data reduces the return on this strategy, which motivates the use of a more robust statistic instead of the rolling mean. The addition of outliers significantly changes the result of the trading strategy, and also has a large bearing on the actual points at which the trading signal changes, showing that this method is not robust to outliers.

In [44]:
fig, ax = plt.subplots(4,2)
fig.suptitle('Comparison of MA Crossover Strategy on Adjusted Closing Prices (Mean)', fontsize=14, fontweight="bold")
fig.set_size_inches(10,12)

total_returns = pd.DataFrame(index=stock_names, columns=["Normal", "Outliers"])

for i,stock in enumerate(stock_names):
    total_returns.loc[stock] = eval_ma_strategy(stock, ax[i])

fig.tight_layout()
total_returns["Difference"] = total_returns["Normal"] - total_returns["Outliers"]
total_returns

Normal  Outliers Difference
DJI   0.016551 -0.032797   0.049348
AAPL  0.457865  0.433691   0.024174
IBM  -0.093396 -0.054028  -0.039369
JPM   0.081476  0.058493   0.022983

<Figure size 720x864 with 8 Axes>

### 4.4.2 Moving Average Crossover (Median)

Since previous experiment have established that using median-based statistics are more robust to outliers than mean-based methods, a variation of this trading strategy is to use the 20 and 50 day moving median instead of the moving mean. While the strategy itself is unfortunately less profitable than the moving mean strategy, we notice that the trading signal does not change much between the set with outliers and the normal data, unlike the previous example where outliers introduce entirely new trading signals.

In [45]:
fig, ax = plt.subplots(4,2)
fig.suptitle('Comparison of MA Crossover Strategy on Adjusted Closing Prices (Median)', fontsize=14, fontweight="bold")
fig.set_size_inches(10,12)

total_returns = pd.DataFrame(index=stock_names, columns=["Normal", "Outliers"])

for i,stock in enumerate(stock_names):
    total_returns.loc[stock] = eval_ma_strategy(stock, ax[i], mean=False)

fig.tight_layout()
total_returns["Difference"] = total_returns["Normal"] - total_returns["Outliers"]
total_returns

Normal  Outliers Difference
DJI  -0.012069 -0.055143   0.043074
AAPL  0.426053  0.388156   0.037897
IBM  -0.130365 -0.130609   0.000244
JPM  -0.301306  0.190908  -0.492215

<Figure size 720x864 with 8 Axes>

# 5. Graphs in Finance

## 5.1. Consider log-returns. Choose up to 10 assets of your choice, explaining your motivations.

This section explores the use of graph data as a basis of analysis for the semiconductor industry in the US between 2015 to 2019, a time when the sector strongly benefitted from the rapid digitalisation of businesses thanks to the increasing adoption of cloud computing and other technologies.

In [46]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import networkx as nx
from scipy.spatial.distance import euclidean
from fastdtw import fastdtw

stocks = pd.read_csv("data/q1/snp_allstocks_2015_2019.csv", index_col=0)
stocks.index = pd.to_datetime(stocks.index)
stock_info = pd.read_csv("data/q1/snp_info.csv", index_col=0)
choices = ["ADI", "AMD", "AVGO", "INTC", "MCHP", "MU", "NVDA", "QCOM", "SWKS", "TXN"]

fig, axes = plt.subplots(1,2)
fig.suptitle("Performance of Semiconductor Industry (2015-2019)", fontsize=16, fontweight="bold")
fig.set_size_inches(10,4)
np.log(stocks[choices]).plot(ax=axes[0], grid=True, title="Log-prices", ylabel="Log-price")
semiconductor_returns = np.log(stocks[choices].dropna(1)).diff(1).dropna()
semiconductor_returns.plot(ax=axes[1], grid=True, title="Log-returns", ylabel="Returns")
fig.tight_layout()

<Figure size 720x288 with 2 Axes>

## 5.2. Construct a graph using your selected stocks based on their correlation matrix. Explain the role of the correlation matrix and show the results as clearly as possible.

In [47]:
semi_corr = semiconductor_returns.corr().round(2)
semi_corr

ADI   AMD  AVGO  INTC  MCHP    MU  NVDA  QCOM  SWKS   TXN
ADI   1.00  0.37  0.59  0.58  0.74  0.52  0.51  0.45  0.66  0.74
AMD   0.37  1.00  0.28  0.29  0.40  0.37  0.42  0.27  0.28  0.37
AVGO  0.59  0.28  1.00  0.45  0.56  0.44  0.43  0.39  0.65  0.57
INTC  0.58  0.29  0.45  1.00  0.60  0.48  0.45  0.39  0.52  0.66
MCHP  0.74  0.40  0.56  0.60  1.00  0.56  0.48  0.41  0.62  0.75
MU    0.52  0.37  0.44  0.48  0.56  1.00  0.46  0.37  0.52  0.53
NVDA  0.51  0.42  0.43  0.45  0.48  0.46  1.00  0.36  0.44  0.53
QCOM  0.45  0.27  0.39  0.39  0.41  0.37  0.36  1.00  0.38  0.44
SWKS  0.66  0.28  0.65  0.52  0.62  0.52  0.44  0.38  1.00  0.63
TXN   0.74  0.37  0.57  0.66  0.75  0.53  0.53  0.44  0.63  1.00

Visual inspection of the correlation matrix above shows that despite all the stocks being from the same industry, not as many of them are strongly correlated as one might think. The highest correlations are between companies which sell low-level components such as MCHP, ADI, TXN and SWKS, which reflects that the demand for electronic components increased in this time. Companies which focused more on higher level products such as AMD and QCOM see lower correlation scores across the board.

## 5.3. Discuss your results, especially whether the topology of your graph is dictated by the nature of the data. Would the re–ordering of graph vertices affect your results? Would the re–ordering of your time–series data affect your results?

As we concluded from the correlation matrix, drawing a graph with any link signifying at least a weak correlation (0.4) results in a highly interconnected mesh except between AMD and QCOM. While this could reflect disjoint business interests, it could also reflect a specific company's dominance. For example, AMD and Intel have long been competitors in desktop CPU and data center businesses, but no link exists between them even when the link threshold is reduced to 0.4 (weak correlations). This is because during this time, Intel held a strong, established market share as a large industry player, and AMD was still a comparatively very small presence by market capitalisation. However, AMD and NVDA's direct competition in the graphics card business is reflected in their log returns, which is shown by the single node connection.

In this case, re-ordering the indices would not affect the correlation between the stock returns, since the mean and variance of the returns would still be unchanged.

In [48]:
# Transform it in a links data frame (3 columns only):
links = semi_corr.stack().reset_index()
links.columns = ['var1', 'var2','value']

# Keep only correlation over a threshold and remove self correlation (cor(A,A)=1)
links_filtered=links.loc[abs(links['value'] > 0.4) & (links['var1'] != links['var2'])]
 
G = nx.from_pandas_edgelist(links_filtered, 'var1', 'var2')
nx.draw(G, with_labels=True, node_color='aqua', node_size=500, edge_color='black', linewidths=1, font_size=10)

<Figure size 432x288 with 1 Axes>

## 5.4. Adopt a distance metric other than correlation. Justify your choice, and repeat Q2 and Q3 above.

Dynamic time warping (DTW) is a measure of similarity between two time series. In general, DTW is a method that calculates an optimal match between two given sequences (e.g. time series) with certain restriction and rules:
>
- Every index from the first sequence must be matched with one or more indices from the other sequence, and vice versa
- The first index from the first sequence must be matched with the first index from the other sequence (but it does not have to be its only match)
- The last index from the first sequence must be matched with the last index from the other sequence (but it does not have to be its only match)
- The mapping of the indices from the first sequence to indices from the other sequence must be monotonically increasing, and vice versa.

From these criteria, we see that dynamic time-warping is able to "stretch" or "compress" regions on a time series to match another, which is important for pattern recognition applications such as in speech processing, when two speakers may be speaking the same words at different speeds. In the context of two stocks from the same sector, news which affects two stocks at slightly different times can be matched this way, and correlations between the two stocks can be drawn.

The calculation below produces a euclidean distance between the two time series after warping them together, a metric known as the warp path. Unlike correlation previously, smaller warp distances indicate more similarity between two series. To determine the threshold for graph plotting, we plot the histogram of the distances.

In [49]:
links = pd.DataFrame(index=list(range(100)),columns=['var1', 'var2','value'])
i = 0
for stock_a in semiconductor_returns.columns:
    for stock_b in semiconductor_returns.columns:
        distance, _ = fastdtw(semiconductor_returns[stock_a], semiconductor_returns[stock_b], dist=euclidean)
        links.iloc[i] = [stock_a, stock_b, distance]
        i += 1

In [50]:
links['value'].plot(kind='hist', bins=30, title="Distribution of Post-DTW Distances", xlabel='Distance', ylabel="Count")

<AxesSubplot:title={'center':'Distribution of Post-DTW Distances'}, ylabel='Frequency'>

<Figure size 432x288 with 1 Axes>

In [51]:
links_filtered=links.loc[abs(links['value'] < 15) & (links['var1'] != links['var2'])]
G = nx.from_pandas_edgelist(links_filtered, 'var1', 'var2')
nx.draw(G, with_labels=True, node_color='aqua', node_size=500, edge_color='black', linewidths=1, font_size=10)

<Figure size 432x288 with 1 Axes>

The resulting graph is very differently connected to the correlation graph obtained before. QCOM has joined the mesh, connected to most of the other nodes. AMD and MU are nowhere to be found, which could be related to these two companies' similar performance pattern in the previous log-price time series, unlike the rest of the stocks. However, this method perhaps is more indicative of overlapping business sectors, since NVDA and AMD are now isolated (or unrelated) to the rest of the network which has a star topology.

Re-indexing the time series in this case would affect the distance metric, since the warped mappings of points between two time series is not necessarily 1-to-1. Different sets of points would therefore be matched if the series were to be re-indexed, and the resulting distances may change.

Since distances and correlations are abstract and do not represent physical quantities, the only way to make conclusive inferences based on graph connections is to find consistent results across an ensemble of sensibly chosen distance metrics. In this case, the only real conclusion we can make between correlation and DTM is that these large-cap companies form an entangled ecosystem for the semiconductor industry in the US, and many of their returns are at least weakly correlated.

## 5.5. Give your intuition on how Q1–Q4 would be affected if you considered raw prices.

As we have discussed heavily in section 1, raw prices are not stationary and over time will often contain trending components for a given stock. Instead of finding patterns in cyclical price fluctuations within the industry, we would instead be correlating the upward trend of the stocks, which would definitely have much more correlated values. As proof below, the correlation matrix higher values overall, and even increasing the threshold for drawing nodes to 0.6 (a moderate correlation), we observe a much more interconnected graph. Similarly, the upward trends would have the same effect on dynamic time warping, and we would expect the distance between warped series to be smaller due to the shared uptrend in prices.

In [52]:
semiconductor_returns = stocks[choices].dropna(1)
price_semi_corr = semiconductor_returns.corr().round(2)
price_semi_corr

ADI   AMD  AVGO  INTC  MCHP    MU  NVDA  QCOM  SWKS   TXN
ADI   1.00  0.83  0.91  0.87  0.95  0.89  0.95  0.13  0.61  0.96
AMD   0.83  1.00  0.79  0.71  0.74  0.67  0.85  0.16  0.29  0.83
AVGO  0.91  0.79  1.00  0.75  0.94  0.73  0.89 -0.05  0.54  0.89
INTC  0.87  0.71  0.75  1.00  0.82  0.90  0.89  0.16  0.35  0.93
MCHP  0.95  0.74  0.94  0.82  1.00  0.85  0.93  0.04  0.61  0.94
MU    0.89  0.67  0.73  0.90  0.85  1.00  0.88  0.28  0.63  0.88
NVDA  0.95  0.85  0.89  0.89  0.93  0.88  1.00  0.09  0.50  0.98
QCOM  0.13  0.16 -0.05  0.16  0.04  0.28  0.09  1.00  0.19  0.14
SWKS  0.61  0.29  0.54  0.35  0.61  0.63  0.50  0.19  1.00  0.46
TXN   0.96  0.83  0.89  0.93  0.94  0.88  0.98  0.14  0.46  1.00

In [53]:
links = price_semi_corr.stack().reset_index()
links.columns = ['var1', 'var2','value']

# Keep only correlation over a threshold and remove self correlation (cor(A,A)=1)
links_filtered=links.loc[abs(links['value'] > 0.5) & (links['var1'] != links['var2'])]
 
G = nx.from_pandas_edgelist(links_filtered, 'var1', 'var2')
nx.draw(G, with_labels=True, node_color='aqua', node_size=500, edge_color='black', linewidths=1, font_size=10)

<Figure size 432x288 with 1 Axes>